# Jupyter notebook for February 18, 2020 presentation
February 18, 2020 presentation of "Translation" at the [Stanford Literary Lab](https://litlab.stanford.edu/).

Quinn Dombrowski, Yulia Ilchuk, J.D. Porter

v. 1.1, published February 18, 2019



## Suggested citation

Quinn Dombrowski. "Jupyter notebook for 'Translation' Literary Lab talk". v. 1.1, published February 18, 2020.


## Abstract
Discussions of translation often focus on the ineffable losses created by moving from one language to another. Yet translation may also leave (or even produce) a residue of the original language, traces of the fact that a text did not start its life in the language the reader encounters. In this project, we use a corpus of short stories translated into English from Russian, French, Spanish, Korean, Italian, Indonesian, German, and Portuguese to examine whether translation leaves a lexical or grammatical trace on its arrival in English and how these traces may vary by language. We hope to uncover the stylistic affordances of translation as such, gesture toward an atlas of the formal effects of translation into English, and potentially generate a few practical findings for translators. 


## Corpus
For our source material, we collected modern (mid-20th/21st century) short stories translated from Indonesian, Italian, Korean, Portuguese, Russian, and Spanish, as well as original stories in English. The corpus isn't republishable due to copyright, but you can find the [metadata about the texts in this CSV](litlab_translations_2020-02-18_corpus_metadata.csv). Each text file contained only the text of the short story; title and author information, trainslator footnotes, etc. were stripped out.

## 1. Basic setup
- Make sure Spacy is installed (e.g. run `pip install spacy` in the Terminal) before running this notebook
- Put each language's texts in its own folder
- In each folder, using the Terminal, run `cat * > all_ru.txt` (replacing *ru* w/ 2-letter abbreviation for the language in question)
- Create a new folder for all these new files, and put them in that directory. Specify the path in the first code block, below

In [1]:
#os is used for things like changing directories and listing files
import os
#io is used for opening and writing files
import io
#itertools is used for some of the iterative code
from itertools import chain
#glob is used to find all the pathnames matching a specified pattern (here, all text files)
import glob

# used for some text matching
import re

# ntlk's sentence tokenizer was easier to use as a first step in sentence length
from nltk import sent_tokenize

# spacy is used for most of the NLP
import spacy
nlp = spacy.load('en_core_web_sm')
from spacy.tokenizer import Tokenizer
from spacy.lemmatizer import Lemmatizer
lemmatizer = Lemmatizer()
from spacy.matcher import Matcher
matcher = Matcher(nlp.vocab)

# scipy stats is used to calculate Fisher's exact
import scipy.stats


#Full path to directory with allru.txt, allen.txt, alles.txt, etc.
sourcefiledirectory = '/Users/qad/Documents/translation/translationcorpus_original'






#Changing the directory to where you've stored the source texts, so you can open them in later code blocks
os.chdir(sourcefiledirectory)

## 2. Get the word count for each corpus
This creates a derivative file, wordcount_XX.txt (with XX replaced by the two-letter language code) with the word count for each language corpus, and prints the results below. You can copy and paste the values printed below into Excel for getting your values for Fisher's exact.

In [5]:
for filename in os.listdir(sourcefiledirectory):
    if filename.startswith("all"):
        outname = filename.replace('all', 'wordcount')
        with open(outname, 'w') as out:
            f = open(filename, 'r')
            text = f.read()
            words = 0
            for wordcount in text.split(" "):
                words += 1
            print(filename)
            print((str(words)))
            out.write(str(words))

all_ru.txt
158965
all_en.txt
202702
all_pt.txt
69059
all_de.txt
88685
all_it.txt
72917
all_ko.txt
296099
all_es.txt
71378
all_id.txt
40654


## 3. Calculating lemma/word count ratio
To get the lemma/word count ratio (on the right side of slide 12), we need to count all the unique lemmas, and compare that to the total word count in (2),  above.

### Creating lemma file
The code block below creates a file, lemmas_XX.txt, that contains the lemma value for each word in the text.

In [6]:
word_count = 0
for filename in os.listdir(sourcefiledirectory):
    if filename.startswith("all"):
        
        f = open(filename, 'r')
        text = f.read()
        lines = sent_tokenize(text)
        outname = filename.replace('all', 'lemmas')
        with open(outname, 'w') as out:
            for line in (lines):
                annotated_line = nlp(line)
                for token in annotated_line:
                    out.write(token.lemma_)
                    out.write(" ")

### Unique lemmas
This creates a file wiht the total count of unique lemmas in each corpus, and also prints those values below.

In [7]:
#count & print to file unique lemmas
for filename in os.listdir(sourcefiledirectory):
    if filename.startswith("lemmas"):
        with open(filename, 'r') as f:
            lines = f.read().splitlines()
            uniques = set()
            for line in lines:
                uniques |= set(line.split())
            outname = filename.replace('lemmas', 'uniquelemmacount')
            with open(outname, 'w') as out:
                out.write(str(len(uniques)))
            print(filename)
            print(len(uniques))

lemmas_es.txt
6620
lemmas_ko.txt
12782
lemmas_id.txt
4884
lemmas_pt.txt
7451
lemmas_it.txt
7794
lemmas_de.txt
8165
lemmas_en.txt
13195
lemmas_ru.txt
11268


### Calculating lemma / token ratio
In Excel (or your favorite software), divide the unique lemma count values with the total word count for each language. The values are in the *Lemmas-tokens* tab of the [working spreadsheet for the presentation](litlab_translations_2020-02-18_fishers_exact_values.xlsx).

## 4. Calculating probability of statistically significant divergence from English for various traits

The traits below (which appear in the table on slide 12) were selected as possible features for distinguishing Russian translations from originally-English texts, and/or were referenced in previous work on translated texts as distinguishing features.

For each trait, we count the occurrences in each of the corpora.

To determine which are statistically significance, we use Fisher's exact test to compare the observed values for the trait to the "null-hypothesis" value, which we base on the observed rate in English. We use the rate the trait occurs in English, and multiply it by the word count for each non-English corpus, to get the "expected" rate for that language if it were to not differ from English more than chance.

Fisher's exact test is calculated with four values, denoted \[a,b\]\[c,d\].
* a: the observed rate for the non-English language
* b: the not-observed rate for the non-English language (word count - a)
* c: the "null-hypothesis" expected value (rate in English x word count)
* d: the "null-hypothesis" expected not-observed value (word count - c)

The [working Excel spreadsheet for the presentation](litlab_translations_2020-02-18_fishers_exact_values.xlsx) has formulas set up for all of these, once you've put in the word count and observed rates for each language (including English).

Because Fisher's exact is looking for the probability that the observed values don't differ from the null-hypothesis values except by chance, **low** values indicate a higher probability that the language has an impact on the occurrence rate of the trait in question.

### 4.1 Determiner count
Russian has many fewer determiners (e.g. no definite / indefinite article), so where determiners exist in translations, they are largely inserted by translators. 

The first code block writes out the spacy IDs for each determiner to a temporary text file, then counts the lines in that text file and writes that count to a file, DET_XX.txt for each language.

The value in DET_XX.txt becomes "a" for calculating Fisher's exact, in the second code block. Value "b" is the total word count. The values of "c" and "d" are calculated in the Excel spreadsheet using the rate for English, multiplied by the word count of the non-English corpus.

In [8]:
#determiners
pattern = [{"POS": "DET", "TAG": "DT"}]

matcher.add("DET", None, pattern)
for filename in os.listdir(sourcefiledirectory):
    if filename.startswith("all"):
        
        f = open(filename, 'r')
        text = f.read()
        lines = sent_tokenize(text)
        outname = filename.replace('all', 'tmp_')
        with open(outname, 'w') as out:
            print(filename)
            for index,line in enumerate(lines):
                annotated_line = nlp(line)
                matches = matcher(annotated_line)
                for match_id, start, end in matches:
                    string_id = nlp.vocab.strings[match_id]  # Get string representation
                    span = annotated_line[start:end]  # The matched span
                    print(match_id, string_id, start, end, span.text)
                    out.write(str(match_id))
                    out.write("\n")
for filename in os.listdir(sourcefiledirectory):
    if filename.startswith("tmp_"):
        with open(filename, 'r') as f:
            outname = filename.replace('tmp_', 'DET_')
            num_lines = 0
            with open(outname, 'w') as out:
                for line in f:
                    num_lines += 1
                print(filename)
                print(num_lines)
                out.write(str(num_lines))
matcher.remove("DET")

all_ru.txt
90 DET 3 4 a
90 DET 9 10 the
90 DET 12 13 the
90 DET 12 13 an
90 DET 20 21 some
90 DET 0 1 That
90 DET 8 9 the
90 DET 16 17 the
90 DET 11 12 the
90 DET 0 1 That
90 DET 1 2 the
90 DET 4 5 a
90 DET 3 4 an
90 DET 8 9 the
90 DET 0 1 That
90 DET 6 7 a
90 DET 9 10 a
90 DET 4 5 the
90 DET 0 1 The
90 DET 0 1 The
90 DET 7 8 the
90 DET 13 14 a
90 DET 0 1 No
90 DET 12 13 the
90 DET 7 8 a
90 DET 19 20 a
90 DET 0 1 A
90 DET 10 11 the
90 DET 13 14 the
90 DET 7 8 the
90 DET 18 19 a
90 DET 3 4 an
90 DET 6 7 a
90 DET 2 3 the
90 DET 17 18 a
90 DET 25 26 the
90 DET 31 32 a
90 DET 37 38 an
90 DET 42 43 a
90 DET 46 47 the
90 DET 8 9 a
90 DET 0 1 This
90 DET 4 5 a
90 DET 10 11 every
90 DET 4 5 no
90 DET 5 6 a
90 DET 2 3 the
90 DET 5 6 the
90 DET 10 11 the
90 DET 17 18 a
90 DET 29 30 the
90 DET 6 7 the
90 DET 13 14 a
90 DET 3 4 the
90 DET 0 1 The
90 DET 2 3 a
90 DET 10 11 the
90 DET 4 5 no
90 DET 11 12 the
90 DET 17 18 The
90 DET 11 12 no
90 DET 14 15 the
90 DET 12 13 a
90 DET 30 31 the
90 DET 4 5

90 DET 0 1 The
90 DET 4 5 the
90 DET 0 1 A
90 DET 4 5 an
90 DET 0 1 The
90 DET 5 6 an
90 DET 0 1 A
90 DET 6 7 the
90 DET 1 2 that
90 DET 4 5 a
90 DET 12 13 the
90 DET 17 18 the
90 DET 22 23 a
90 DET 27 28 the
90 DET 31 32 a
90 DET 36 37 a
90 DET 2 3 no
90 DET 9 10 the
90 DET 15 16 the
90 DET 20 21 the
90 DET 4 5 the
90 DET 9 10 that
90 DET 14 15 The
90 DET 24 25 any
90 DET 28 29 the
90 DET 35 36 the
90 DET 4 5 the
90 DET 2 3 a
90 DET 10 11 a
90 DET 14 15 the
90 DET 4 5 a
90 DET 4 5 another
90 DET 0 1 That
90 DET 5 6 a
90 DET 13 14 the
90 DET 2 3 the
90 DET 7 8 the
90 DET 13 14 the
90 DET 19 20 a
90 DET 0 1 The
90 DET 12 13 the
90 DET 21 22 the
90 DET 28 29 the
90 DET 2 3 the
90 DET 8 9 the
90 DET 13 14 the
90 DET 1 2 the
90 DET 7 8 the
90 DET 18 19 the
90 DET 21 22 the
90 DET 28 29 the
90 DET 5 6 the
90 DET 8 9 the
90 DET 28 29 the
90 DET 31 32 the
90 DET 34 35 the
90 DET 3 4 the
90 DET 19 20 the
90 DET 3 4 the
90 DET 7 8 some
90 DET 17 18 any
90 DET 37 38 the
90 DET 42 43 the
90 DET 4

90 DET 5 6 some
90 DET 8 9 an
90 DET 12 13 no
90 DET 18 19 the
90 DET 7 8 a
90 DET 5 6 the
90 DET 0 1 Some
90 DET 2 3 the
90 DET 2 3 an
90 DET 6 7 the
90 DET 7 8 an
90 DET 18 19 the
90 DET 21 22 the
90 DET 1 2 that
90 DET 6 7 the
90 DET 5 6 the
90 DET 6 7 a
90 DET 12 13 some
90 DET 14 15 the
90 DET 4 5 a
90 DET 7 8 a
90 DET 12 13 any
90 DET 15 16 any
90 DET 4 5 a
90 DET 8 9 the
90 DET 16 17 another
90 DET 5 6 a
90 DET 0 1 A
90 DET 7 8 every
90 DET 0 1 The
90 DET 18 19 the
90 DET 21 22 that
90 DET 5 6 the
90 DET 10 11 the
90 DET 16 17 the
90 DET 19 20 an
90 DET 23 24 a
90 DET 1 2 this
90 DET 2 3 the
90 DET 10 11 the
90 DET 13 14 the
90 DET 21 22 a
90 DET 1 2 this
90 DET 6 7 the
90 DET 15 16 the
90 DET 23 24 the
90 DET 5 6 the
90 DET 8 9 the
90 DET 15 16 no
90 DET 14 15 those
90 DET 3 4 the
90 DET 8 9 the
90 DET 1 2 the
90 DET 6 7 that
90 DET 2 3 the
90 DET 16 17 a
90 DET 1 2 this
90 DET 3 4 a
90 DET 11 12 the
90 DET 0 1 The
90 DET 7 8 the
90 DET 10 11 the
90 DET 21 22 the
90 DET 0 1 An


90 DET 0 1 That
90 DET 8 9 the
90 DET 7 8 the
90 DET 1 2 the
90 DET 10 11 a
90 DET 0 1 That
90 DET 0 1 A
90 DET 1 2 that
90 DET 10 11 a
90 DET 14 15 the
90 DET 5 6 the
90 DET 12 13 the
90 DET 3 4 the
90 DET 17 18 the
90 DET 13 14 a
90 DET 26 27 the
90 DET 0 1 All
90 DET 23 24 the
90 DET 3 4 the
90 DET 9 10 a
90 DET 15 16 the
90 DET 2 3 the
90 DET 0 1 The
90 DET 6 7 a
90 DET 7 8 The
90 DET 11 12 a
90 DET 13 14 a
90 DET 21 22 a
90 DET 10 11 all
90 DET 13 14 a
90 DET 0 1 The
90 DET 6 7 the
90 DET 14 15 the
90 DET 4 5 the
90 DET 8 9 the
90 DET 0 1 A
90 DET 9 10 the
90 DET 0 1 The
90 DET 9 10 the
90 DET 13 14 the
90 DET 0 1 The
90 DET 1 2 that
90 DET 7 8 a
90 DET 1 2 the
90 DET 8 9 no
90 DET 11 12 the
90 DET 18 19 the
90 DET 9 10 this
90 DET 12 13 any
90 DET 15 16 the
90 DET 22 23 the
90 DET 0 1 A
90 DET 5 6 a
90 DET 11 12 the
90 DET 24 25 a
90 DET 28 29 the
90 DET 31 32 The
90 DET 5 6 the
90 DET 12 13 that
90 DET 1 2 the
90 DET 8 9 the
90 DET 6 7 the
90 DET 10 11 that
90 DET 0 1 The
90 DET

90 DET 4 5 any
90 DET 5 6 the
90 DET 10 11 all
90 DET 4 5 the
90 DET 7 8 a
90 DET 11 12 every
90 DET 17 18 the
90 DET 2 3 the
90 DET 15 16 the
90 DET 0 1 The
90 DET 7 8 the
90 DET 0 1 That
90 DET 11 12 the
90 DET 14 15 the
90 DET 17 18 that
90 DET 0 1 All
90 DET 3 4 the
90 DET 13 14 any
90 DET 12 13 the
90 DET 0 1 The
90 DET 1 2 the
90 DET 3 4 a
90 DET 48 49 the
90 DET 11 12 the
90 DET 14 15 A
90 DET 19 20 the
90 DET 23 24 a
90 DET 27 28 the
90 DET 31 32 the
90 DET 5 6 the
90 DET 8 9 a
90 DET 3 4 a
90 DET 0 1 A
90 DET 9 10 a
90 DET 0 1 A
90 DET 3 4 a
90 DET 10 11 a
90 DET 0 1 The
90 DET 7 8 the
90 DET 11 12 this
90 DET 20 21 the
90 DET 0 1 A
90 DET 6 7 a
90 DET 23 24 that
90 DET 37 38 an
90 DET 7 8 this
90 DET 12 13 all
90 DET 9 10 the
90 DET 3 4 the
90 DET 3 4 the
90 DET 4 5 the
90 DET 3 4 a
90 DET 19 20 a
90 DET 28 29 a
90 DET 4 5 the
90 DET 2 3 no
90 DET 0 1 The
90 DET 9 10 the
90 DET 12 13 the
90 DET 2 3 a
90 DET 18 19 a
90 DET 15 16 no
90 DET 2 3 the
90 DET 10 11 a
90 DET 16 17 th

...

90 DET 11 12 the
90 DET 15 16 the
90 DET 2 3 the
90 DET 5 6 the
90 DET 13 14 the
90 DET 7 8 a
90 DET 3 4 this
90 DET 0 1 The
90 DET 5 6 this
90 DET 1 2 the
90 DET 0 1 A
90 DET 8 9 this
90 DET 29 30 a
90 DET 3 4 the
90 DET 9 10 the
90 DET 3 4 the
90 DET 7 8 the
90 DET 13 14 a
90 DET 4 5 the
90 DET 0 1 The
90 DET 16 17 the
90 DET 2 3 an
90 DET 9 10 the
90 DET 13 14 the
90 DET 17 18 a
90 DET 1 2 that
90 DET 0 1 The
90 DET 6 7 any
90 DET 9 10 the
90 DET 15 16 each
90 DET 18 19 the
90 DET 1 2 a
90 DET 0 1 The
90 DET 0 1 The
90 DET 3 4 a
90 DET 15 16 the
90 DET 18 19 the
90 DET 1 2 That
90 DET 1 2 The
90 DET 0 1 The
90 DET 0 1 That
90 DET 0 1 The
90 DET 7 8 the
90 DET 4 5 these
90 DET 1 2 That
90 DET 4 5 some
90 DET 0 1 A
90 DET 3 4 both
90 DET 8 9 the
90 DET 1 2 The
90 DET 3 4 the
90 DET 2 3 the
90 DET 3 4 that
90 DET 2 3 this
90 DET 0 1 The
90 DET 6 7 the
90 DET 3 4 the
90 DET 0 1 A
90 DET 6 7 a
90 DET 4 5 the
90 DET 7 8 a
90 DET 1 2 The
90 DET 0 1 A
90 DET 1 2 A
90 DET 1 2 The
90 DET 5 6 

90 DET 7 8 no
90 DET 5 6 a
90 DET 13 14 the
90 DET 16 17 this
90 DET 0 1 A
90 DET 1 2 that
90 DET 0 1 The
90 DET 3 4 this
90 DET 0 1 The
90 DET 9 10 those
90 DET 11 12 a
90 DET 15 16 the
90 DET 4 5 no
90 DET 9 10 the
90 DET 12 13 this
90 DET 4 5 the
90 DET 1 2 a
90 DET 7 8 the
90 DET 2 3 the
90 DET 6 7 the
90 DET 10 11 the
90 DET 0 1 The
90 DET 11 12 the
90 DET 15 16 the
90 DET 19 20 the
90 DET 3 4 a
90 DET 9 10 an
90 DET 3 4 a
90 DET 2 3 an
90 DET 5 6 an
90 DET 5 6 any
90 DET 21 22 any
90 DET 24 25 a
90 DET 4 5 an
90 DET 14 15 a
90 DET 2 3 those
90 DET 7 8 the
90 DET 10 11 an
90 DET 3 4 the
90 DET 6 7 a
90 DET 4 5 an
90 DET 14 15 a
90 DET 9 10 a
90 DET 6 7 a
90 DET 10 11 the
90 DET 14 15 a
90 DET 1 2 a
90 DET 19 20 this
90 DET 29 30 the
90 DET 32 33 the
90 DET 0 1 The
90 DET 3 4 a
90 DET 9 10 a
90 DET 15 16 the
90 DET 18 19 the
90 DET 3 4 the
90 DET 1 2 the
90 DET 18 19 the
90 DET 2 3 a
90 DET 2 3 the
90 DET 6 7 the
90 DET 0 1 The
90 DET 7 8 the
90 DET 3 4 that
90 DET 2 3 a
90 DET 0 1

90 DET 17 18 no
90 DET 7 8 a
90 DET 5 6 the
90 DET 12 13 the
90 DET 7 8 an
90 DET 16 17 both
90 DET 3 4 a
90 DET 8 9 a
90 DET 15 16 a
90 DET 0 1 That
90 DET 2 3 the
90 DET 6 7 that
90 DET 4 5 the
90 DET 7 8 that
90 DET 19 20 the
90 DET 3 4 the
90 DET 6 7 a
90 DET 16 17 the
90 DET 19 20 the
90 DET 5 6 the
90 DET 9 10 the
90 DET 13 14 the
90 DET 16 17 the
90 DET 1 2 the
90 DET 0 1 The
90 DET 11 12 the
90 DET 14 15 the
90 DET 26 27 a
90 DET 29 30 the
90 DET 41 42 the
90 DET 48 49 the
90 DET 7 8 an
90 DET 7 8 those
90 DET 6 7 the
90 DET 16 17 a
90 DET 0 1 Both
90 DET 0 1 The
90 DET 8 9 the
90 DET 15 16 the
90 DET 7 8 the
90 DET 11 12 the
90 DET 3 4 the
90 DET 6 7 the
90 DET 6 7 a
90 DET 3 4 the
90 DET 0 1 The
90 DET 4 5 the
90 DET 15 16 the
90 DET 24 25 a
90 DET 9 10 a
90 DET 13 14 a
90 DET 16 17 a
90 DET 0 1 The
90 DET 0 1 The
90 DET 16 17 a
90 DET 1 2 this
90 DET 3 4 the
90 DET 0 1 That
90 DET 5 6 a
90 DET 0 1 A
90 DET 6 7 the
90 DET 12 13 that
90 DET 9 10 the
90 DET 12 13 a
90 DET 1 2 t

90 DET 0 1 The
90 DET 14 15 a
90 DET 20 21 the
90 DET 29 30 a
90 DET 5 6 the
90 DET 14 15 A
90 DET 6 7 that
90 DET 15 16 the
90 DET 9 10 the
90 DET 3 4 the
90 DET 4 5 the
90 DET 8 9 the
90 DET 11 12 the
90 DET 0 1 The
90 DET 3 4 the
90 DET 7 8 the
90 DET 16 17 the
90 DET 0 1 A
90 DET 3 4 a
90 DET 8 9 the
90 DET 13 14 the
90 DET 18 19 the
90 DET 1 2 the
90 DET 5 6 the
90 DET 8 9 the
90 DET 18 19 the
90 DET 27 28 the
90 DET 30 31 the
90 DET 7 8 those
90 DET 3 4 the
90 DET 9 10 the
90 DET 19 20 this
90 DET 0 1 A
90 DET 15 16 the
90 DET 19 20 the
90 DET 15 16 some
90 DET 22 23 the
90 DET 26 27 the
90 DET 7 8 a
90 DET 23 24 the
90 DET 4 5 the
90 DET 16 17 a
90 DET 2 3 the
90 DET 7 8 a
90 DET 8 9 a
90 DET 14 15 that
90 DET 5 6 a
90 DET 2 3 no
90 DET 19 20 a
90 DET 27 28 each
90 DET 2 3 the
90 DET 10 11 the
90 DET 6 7 a
90 DET 9 10 that
90 DET 14 15 the
90 DET 1 2 the
90 DET 4 5 the
90 DET 7 8 the
90 DET 0 1 The
90 DET 2 3 the
90 DET 3 4 the
90 DET 6 7 no
90 DET 10 11 the
90 DET 4 5 that
90 D

90 DET 5 6 the
90 DET 8 9 the
90 DET 5 6 the
90 DET 3 4 the
90 DET 7 8 the
90 DET 0 1 The
90 DET 8 9 a
90 DET 13 14 the
90 DET 0 1 A
90 DET 7 8 the
90 DET 15 16 the
90 DET 23 24 the
90 DET 0 1 Any
90 DET 5 6 The
90 DET 10 11 the
90 DET 21 22 a
90 DET 28 29 a
90 DET 0 1 All
90 DET 0 1 The
90 DET 1 2 a
90 DET 4 5 the
90 DET 3 4 the
90 DET 6 7 the
90 DET 0 1 The
90 DET 10 11 the
90 DET 13 14 the
90 DET 0 1 The
90 DET 5 6 the
90 DET 8 9 the
90 DET 13 14 the
90 DET 16 17 the
90 DET 4 5 a
90 DET 8 9 the
90 DET 0 1 The
90 DET 2 3 the
90 DET 6 7 the
90 DET 15 16 the
90 DET 0 1 The
90 DET 11 12 no
90 DET 0 1 The
90 DET 7 8 the
90 DET 1 2 a
90 DET 16 17 a
90 DET 22 23 the
90 DET 0 1 Every
90 DET 6 7 no
90 DET 16 17 the
90 DET 18 19 a
90 DET 8 9 a
90 DET 12 13 that
90 DET 3 4 the
90 DET 0 1 The
90 DET 0 1 The
90 DET 4 5 no
90 DET 7 8 the
90 DET 2 3 the
90 DET 12 13 the
90 DET 17 18 the
90 DET 2 3 the
90 DET 4 5 a
90 DET 9 10 the
90 DET 0 1 An
90 DET 4 5 that
90 DET 3 4 the
90 DET 8 9 the
90 DET 1

In [10]:
#Fisher's exact for determiners

print('determiners')
print('e.g. a, the, that')
#[a,b][c,d]
#ru
oddsratio, pvalue = scipy.stats.fisher_exact([[17495, 141470], [16767, 142198]])
print('ru')
print(pvalue)

#pt
oddsratio, pvalue = scipy.stats.fisher_exact([[8555, 60504], [7284, 61775]])
print('pt')
print(pvalue)

#it
oddsratio, pvalue = scipy.stats.fisher_exact([[8627, 64290], [7691, 65226]])
print('it')
print(pvalue)

#es
oddsratio, pvalue = scipy.stats.fisher_exact([[7420, 63958], [7529, 63849]])
print('es')
print(pvalue)

#id
oddsratio, pvalue = scipy.stats.fisher_exact([[4149, 36505], [4288, 36366]])
print('id')
print(pvalue)

#de
oddsratio, pvalue = scipy.stats.fisher_exact([[10275, 78410], [9354, 79331]])
print('de')
print(pvalue)

#ko
oddsratio, pvalue = scipy.stats.fisher_exact([[33865, 262234], [31231, 264868]])
print('ko')
print(pvalue)

determiners
e.g. a, the, that
ru
3.208056338198617e-05
pt
7.370645952797856e-27
it
7.927810873090188e-15
es
0.3505363819779893
id
0.11251045153096118
de
3.300975274647613e-12
ko
7.430493302787653e-28


### 4.2 Gerund use
Russian more frequently uses constructions like "*Going* outside, she saw..." so we wanted to see if there were more constructions with gerund without an auxiliary verb beforehand.

We also wanted to look at gerund usage *with* auxiliary verbs, because that could reflect decisions on how to translate Russian aspect.

For gerunds with auxiliaries, we used word count / 2 (rather than word count) because it's a bigram, meaning the maximum possible value would then need to be word count divided in half (for a text that contained, for instance, nothing but repetitions of "was reading").

#### Gerund w/o aux

In [11]:
#gerund/present particle w/o aux
pattern = [{"DEP": {"NOT_IN": ["aux"]}}, {"TAG": "VBG"}]

matcher.add("gerund", None, pattern)
for filename in os.listdir(sourcefiledirectory):
    if filename.startswith("all"):
        
        f = open(filename, 'r')
        text = f.read()
        lines = sent_tokenize(text)
        outname = filename.replace('all', 'tmp_')
        with open(outname, 'w') as out:
            print(filename)
            for index,line in enumerate(lines):
                annotated_line = nlp(line)
                matches = matcher(annotated_line)
                for match_id, start, end in matches:
                    string_id = nlp.vocab.strings[match_id]  # Get string representation
                    span = annotated_line[start:end]  # The matched span
                    print(match_id, string_id, start, end, span.text)
                    out.write(str(match_id))
                    out.write("\n")
for filename in os.listdir(sourcefiledirectory):
    if filename.startswith("tmp_"):
        with open(filename, 'r') as f:
            outname = filename.replace('tmp_', 'gerund_')
            num_lines = 0
            with open('outname', 'w') as out:
                for line in f:
                    num_lines += 1
                print(filename)
                print(num_lines)
                out.write(str(num_lines))
matcher.remove("gerund")

all_ru.txt
12539000998014861558 gerund 7 9 

Leaving
12539000998014861558 gerund 17 19 not waiting
12539000998014861558 gerund 2 4 just lying
12539000998014861558 gerund 14 16 , disintegrating
12539000998014861558 gerund 10 12 , snoring
12539000998014861558 gerund 9 11 keep yawning
12539000998014861558 gerund 11 13 and nodding
12539000998014861558 gerund 9 11 still sleeping
12539000998014861558 gerund 17 19 , exhaling
12539000998014861558 gerund 11 13 n’t sleeping
12539000998014861558 gerund 40 42 , forming
12539000998014861558 gerund 5 7 , drawing
12539000998014861558 gerund 0 2 This drawing
12539000998014861558 gerund 3 5 fastidiously interrogating
12539000998014861558 gerund 10 12 the drying
12539000998014861558 gerund 12 14 , kneading
12539000998014861558 gerund 0 2 Without glancing
12539000998014861558 gerund 2 4 like being
12539000998014861558 gerund 2 4 , spitting
12539000998014861558 gerund 9 11 a screaming
12539000998014861558 gerund 11 13 start howling
12539000998014861558 ge

12539000998014861558 gerund 10 12 , turning
12539000998014861558 gerund 12 14 already lying
12539000998014861558 gerund 12 14 even thinking
12539000998014861558 gerund 19 21 an aging
12539000998014861558 gerund 8 10 , steadying
12539000998014861558 gerund 15 17 no burning
12539000998014861558 gerund 0 2 After crossing
12539000998014861558 gerund 12 14 from watching
12539000998014861558 gerund 12 14 , muttering
12539000998014861558 gerund 23 25 start moving
12539000998014861558 gerund 3 5 even thinking
12539000998014861558 gerund 4 6 in thinking
12539000998014861558 gerund 4 6 -affirming
12539000998014861558 gerund 6 8 curses coming
12539000998014861558 gerund 5 7 you doing
12539000998014861558 gerund 16 18 without answering
12539000998014861558 gerund 27 29 a cooling
12539000998014861558 gerund 2 4 you trying
12539000998014861558 gerund 10 12 all going
12539000998014861558 gerund 22 24 , shaking
12539000998014861558 gerund 23 25 , threatening
12539000998014861558 gerund 3 5 you going
1

12539000998014861558 gerund 8 10 bother asking
12539000998014861558 gerund 6 8 crowd filling
12539000998014861558 gerund 6 8 few remaining
12539000998014861558 gerund 14 16 of waiting
12539000998014861558 gerund 5 7 hours killing
12539000998014861558 gerund 8 10 , letting
12539000998014861558 gerund 3 5 , touching
12539000998014861558 gerund 24 26 we going
12539000998014861558 gerund 2 4 -looking
12539000998014861558 gerund 6 8 and drinking
12539000998014861558 gerund 9 11 , turning
12539000998014861558 gerund 7 9 though straining
12539000998014861558 gerund 16 18 , walking
12539000998014861558 gerund 5 7 someone cracking
12539000998014861558 gerund 10 12 , pressing
12539000998014861558 gerund 5 7 , looping
12539000998014861558 gerund 7 9 when tailing
12539000998014861558 gerund 13 15 Annie going
12539000998014861558 gerund 19 21 windows reaching
12539000998014861558 gerund 3 5 all moving
12539000998014861558 gerund 2 4 lock barring
12539000998014861558 gerund 3 5 , moving
125390009980

12539000998014861558 gerund 21 23 of touching
12539000998014861558 gerund 27 29 , snaking
12539000998014861558 gerund 32 34 the falling
12539000998014861558 gerund 4 6 still smoldering
12539000998014861558 gerund 12 14 started cooling
12539000998014861558 gerund 7 9 despite having
12539000998014861558 gerund 3 5 finished giving
12539000998014861558 gerund 6 8 enjoyed talking
12539000998014861558 gerund 3 5 of having
12539000998014861558 gerund 9 11 , stuttering
12539000998014861558 gerund 12 14 , resuming
12539000998014861558 gerund 13 15 considering acquiring
12539000998014861558 gerund 6 8 , producing
12539000998014861558 gerund 11 13 , assuming
12539000998014861558 gerund 3 5 n’t looking
12539000998014861558 gerund 34 36 than getting
12539000998014861558 gerund 4 6 a practicing
12539000998014861558 gerund 15 17 for acclimatizing
12539000998014861558 gerund 18 20 the leading
12539000998014861558 gerund 22 24 include replenishing
12539000998014861558 gerund 28 30 , restoring
125390009

12539000998014861558 gerund 6 8 , chafing
12539000998014861558 gerund 10 12 , pulling
12539000998014861558 gerund 3 5 door using
12539000998014861558 gerund 8 10 , honing
12539000998014861558 gerund 1 3 ’m waiting
12539000998014861558 gerund 3 5 , turning
12539000998014861558 gerund 8 10 , saturating
12539000998014861558 gerund 10 12 their stinking
12539000998014861558 gerund 10 12 icicles hanging
12539000998014861558 gerund 5 7 ’re going
12539000998014861558 gerund 15 17 clothes soaking
12539000998014861558 gerund 4 6 in sagging
12539000998014861558 gerund 10 12 , breathing
12539000998014861558 gerund 11 13 overcoat trailing
12539000998014861558 gerund 33 35 , clutching
12539000998014861558 gerund 2 4 like trying
12539000998014861558 gerund 30 32 ’m standing
12539000998014861558 gerund 30 32 before slithering
12539000998014861558 gerund 4 6 out sounding
12539000998014861558 gerund 2 4 ’m taking
12539000998014861558 gerund 21 23 started chattering
12539000998014861558 gerund 6 8 , prom

...

12539000998014861558 gerund 95 97 words being
12539000998014861558 gerund 10 12 , checking
12539000998014861558 gerund 4 6 from responding
12539000998014861558 gerund 19 21 face flashing
12539000998014861558 gerund 21 23 mother discussing
12539000998014861558 gerund 62 64 of failing
12539000998014861558 gerund 12 14 painfully struggling
12539000998014861558 gerund 3 5 off reading
12539000998014861558 gerund 21 23 , setting
12539000998014861558 gerund 29 31 seconds clouding
12539000998014861558 gerund 8 10 book waiting
12539000998014861558 gerund 35 37 , forcing
12539000998014861558 gerund 8 10 hillside blazing
12539000998014861558 gerund 17 19 trees shimmering
12539000998014861558 gerund 11 13 without being
12539000998014861558 gerund 5 7 by watching
12539000998014861558 gerund 10 12 without being
12539000998014861558 gerund 19 21 somehow avenging
12539000998014861558 gerund 5 7 in imagining
12539000998014861558 gerund 15 17 the following
12539000998014861558 gerund 13 15 , expecting
1

12539000998014861558 gerund 0 2 While going
12539000998014861558 gerund 1 3 if waiting
12539000998014861558 gerund 12 14 , knowing
12539000998014861558 gerund 9 11 on maintaining
12539000998014861558 gerund 28 30 stopped playing
12539000998014861558 gerund 19 21 the following
12539000998014861558 gerund 2 4 stopped talking
12539000998014861558 gerund 12 14 before reading
all_id.txt
12539000998014861558 gerund 8 10 the following
12539000998014861558 gerund 14 16 that working
12539000998014861558 gerund 41 43 to rifling
12539000998014861558 gerund 39 41 anything having
12539000998014861558 gerund 8 10 for being
12539000998014861558 gerund 12 14 ” adding
12539000998014861558 gerund 11 13 about working
12539000998014861558 gerund 6 8 days dreaming
12539000998014861558 gerund 20 22 , thinking
12539000998014861558 gerund 21 23 of losing
12539000998014861558 gerund 33 35 up having
12539000998014861558 gerund 30 32 up having
12539000998014861558 gerund 12 14 , expecting
12539000998014861558 ge

12539000998014861558 gerund 6 8 comfortable being
12539000998014861558 gerund 5 7 vehicles coming
12539000998014861558 gerund 17 19 , burning
12539000998014861558 gerund 0 2 After having
12539000998014861558 gerund 4 6 , hoping
12539000998014861558 gerund 7 9 a passing
12539000998014861558 gerund 2 4 of decaying
12539000998014861558 gerund 11 13 now sitting
12539000998014861558 gerund 11 13 addict suffering
12539000998014861558 gerund 2 4 , trying
12539000998014861558 gerund 14 16 start thinking
12539000998014861558 gerund 1 3 stopped leaning
12539000998014861558 gerund 3 5 you telling
12539000998014861558 gerund 7 9 for killing
12539000998014861558 gerund 5 7 not being
12539000998014861558 gerund 15 17 from being
12539000998014861558 gerund 9 11 avoid asking
12539000998014861558 gerund 2 4 now heading
12539000998014861558 gerund 7 9 head bobbing
12539000998014861558 gerund 19 21 , coming
12539000998014861558 gerund 10 12 of transforming
12539000998014861558 gerund 12 14 , producing
12

12539000998014861558 gerund 5 7 emphasize standing
12539000998014861558 gerund 9 11 not wanting
12539000998014861558 gerund 6 8 indeed forgiving
12539000998014861558 gerund 15 17 when viewing
12539000998014861558 gerund 5 7 a dazzling
12539000998014861558 gerund 4 6 , recalling
12539000998014861558 gerund 1 3 if experiencing
12539000998014861558 gerund 12 14 one altering
12539000998014861558 gerund 6 8 now smiling
12539000998014861558 gerund 3 5 you talking
12539000998014861558 gerund 11 13 not going
12539000998014861558 gerund 15 17 , sniggering
12539000998014861558 gerund 2 4 between dozing
12539000998014861558 gerund 4 6 and trying
12539000998014861558 gerund 8 10 face shining
12539000998014861558 gerund 10 12 already waiting
12539000998014861558 gerund 40 42 , springing
12539000998014861558 gerund 21 23 , hiding
12539000998014861558 gerund 1 3 While correcting
12539000998014861558 gerund 5 7 wordlessly watching
12539000998014861558 gerund 11 13 , living
12539000998014861558 gerund 

12539000998014861558 gerund 14 16 older sibling
12539000998014861558 gerund 13 15 , smiling
12539000998014861558 gerund 6 8 but having
12539000998014861558 gerund 37 39 stream trying
12539000998014861558 gerund 0 2 After being
12539000998014861558 gerund 0 2 And watching
12539000998014861558 gerund 6 8 , being
12539000998014861558 gerund 20 22 stopped being
12539000998014861558 gerund 12 14 whistle indicating
12539000998014861558 gerund 23 25 before heading
12539000998014861558 gerund 4 6 ’re wondering
12539000998014861558 gerund 13 15 stood smiling
12539000998014861558 gerund 33 35 , causing
12539000998014861558 gerund 8 10 , carrying
12539000998014861558 gerund 12 14 bag containing
12539000998014861558 gerund 6 8 , touching
12539000998014861558 gerund 4 6 missed reading
12539000998014861558 gerund 20 22 said grinning
12539000998014861558 gerund 20 22 , helping
12539000998014861558 gerund 25 27 , laughing
12539000998014861558 gerund 27 29 , observing
12539000998014861558 gerund 50 52 

In [12]:
#Gerund (w/o aux)

print('gerund w/o aux')
print('e.g. Without glancing')
#ru
oddsratio, pvalue = scipy.stats.fisher_exact([[2865, 156100], [2956, 156009]])
print('ru')
print(pvalue)

#pt
oddsratio, pvalue = scipy.stats.fisher_exact([[1467, 67592], [1284, 67775]])
print('pt')
print(pvalue)

#it
oddsratio, pvalue = scipy.stats.fisher_exact([[1291, 71626], [1356, 71561]])
print('it')
print(pvalue)

#es
oddsratio, pvalue = scipy.stats.fisher_exact([[1315, 70063], [1327, 70051]])
print('es')
print(pvalue)

#id
oddsratio, pvalue = scipy.stats.fisher_exact([[711, 39943], [756, 39898]])
print('id')
print(pvalue)

#de
oddsratio, pvalue = scipy.stats.fisher_exact([[1594, 87091], [1649, 87036]])
print('de')
print(pvalue)

#ko
oddsratio, pvalue = scipy.stats.fisher_exact([[5634, 290465], [5506, 290593]])
print('ko')
print(pvalue)


gerund w/o aux
e.g. Without glancing
ru
0.23381825254478564
pt
0.0004545402928359299
it
0.20932722763853323
es
0.8289814050677836
id
0.24633000338570393
de
0.3385511688185772
ko
0.22446206371579275


#### Gerund w/ aux

In [13]:
#aux + gerund/present particle
pattern = [{"DEP": "aux"}, {"TAG": "VBG"}]

matcher.add("gerund", None, pattern)
for filename in os.listdir(sourcefiledirectory):
    if filename.startswith("all"):
        
        f = open(filename, 'r')
        text = f.read()
        lines = sent_tokenize(text)
        outname = filename.replace('all', 'tmp_')
        with open(outname, 'w') as out:
            print(filename)
            for index,line in enumerate(lines):
                annotated_line = nlp(line)
                matches = matcher(annotated_line)
                for match_id, start, end in matches:
                    string_id = nlp.vocab.strings[match_id]  # Get string representation
                    span = annotated_line[start:end]  # The matched span
                    print(match_id, string_id, start, end, span.text)
                    out.write(str(match_id))
                    out.write("\n")
for filename in os.listdir(sourcefiledirectory):
    if filename.startswith("tmp_"):
        with open(filename, 'r') as f:
            outname = filename.replace('tmp_', 'AUXgerund_')
            with open(outname, 'w') as out:
                num_lines = 0
                for line in f:
                    num_lines += 1
                print(filename)
                print(num_lines)
                out.write(str(num_lines))
matcher.remove("gerund")

all_ru.txt
12539000998014861558 gerund 2 4 get going
12539000998014861558 gerund 29 31 was playing
12539000998014861558 gerund 10 12 was doing
12539000998014861558 gerund 1 3 were rolling
12539000998014861558 gerund 1 3 was hoping
12539000998014861558 gerund 26 28 was feeling
12539000998014861558 gerund 2 4 was reaping
12539000998014861558 gerund 8 10 to according
12539000998014861558 gerund 9 11 be raining
12539000998014861558 gerund 31 33 was dealing
12539000998014861558 gerund 10 12 was carrying
12539000998014861558 gerund 5 7 was being
12539000998014861558 gerund 2 4 was lying
12539000998014861558 gerund 5 7 been watching
12539000998014861558 gerund 6 8 was grabbing
12539000998014861558 gerund 1 3 was running
12539000998014861558 gerund 2 4 was choking
12539000998014861558 gerund 11 13 was writhing
12539000998014861558 gerund 12 14 was trying
12539000998014861558 gerund 20 22 was eating
12539000998014861558 gerund 18 20 was wearing
12539000998014861558 gerund 9 11 was holding
12539

12539000998014861558 gerund 10 12 are sleeping
12539000998014861558 gerund 1 3 is handing
12539000998014861558 gerund 12 14 is leaning
12539000998014861558 gerund 6 8 been counting
12539000998014861558 gerund 6 8 be working
12539000998014861558 gerund 24 26 was wearing
12539000998014861558 gerund 3 5 was thinking
12539000998014861558 gerund 2 4 were trembling
12539000998014861558 gerund 4 6 are giving
12539000998014861558 gerund 17 19 been feeling
12539000998014861558 gerund 11 13 be drinking
12539000998014861558 gerund 9 11 am going
12539000998014861558 gerund 10 12 be swimming
12539000998014861558 gerund 1 3 was sitting
12539000998014861558 gerund 11 13 was getting
12539000998014861558 gerund 1 3 was shaking
12539000998014861558 gerund 7 9 was standing
12539000998014861558 gerund 16 18 was faking
12539000998014861558 gerund 1 3 was sobbing
12539000998014861558 gerund 1 3 was staring
12539000998014861558 gerund 2 4 was leaving
12539000998014861558 gerund 2 4 be looking
125390009980148

12539000998014861558 gerund 25 27 was going
12539000998014861558 gerund 3 5 is going
12539000998014861558 gerund 33 35 been running
12539000998014861558 gerund 8 10 are bringing
12539000998014861558 gerund 6 8 been forgetting
12539000998014861558 gerund 1 3 was standing
12539000998014861558 gerund 12 14 was sitting
12539000998014861558 gerund 50 52 was lying
12539000998014861558 gerund 10 12 be lying
12539000998014861558 gerund 19 21 be edifying
12539000998014861558 gerund 33 35 was hanging
12539000998014861558 gerund 1 3 was wearing
12539000998014861558 gerund 11 13 been seeing
12539000998014861558 gerund 2 4 been counting
12539000998014861558 gerund 9 11 was living
12539000998014861558 gerund 16 18 been hoping
12539000998014861558 gerund 6 8 been counting
12539000998014861558 gerund 10 12 were drinking
12539000998014861558 gerund 5 7 was crossing
12539000998014861558 gerund 1 3 was leafing
12539000998014861558 gerund 10 12 was sitting
12539000998014861558 gerund 1 3 was running
12539

12539000998014861558 gerund 1 3 were talking
12539000998014861558 gerund 25 27 were talking
12539000998014861558 gerund 12 14 was bending
12539000998014861558 gerund 43 45 is disappearing
12539000998014861558 gerund 3 5 was hanging
12539000998014861558 gerund 5 7 is sitting
12539000998014861558 gerund 18 20 was being
12539000998014861558 gerund 32 34 am studying
12539000998014861558 gerund 42 44 is gathering
12539000998014861558 gerund 46 48 are swirling
12539000998014861558 gerund 5 7 was doing
12539000998014861558 gerund 8 10 are breaking
12539000998014861558 gerund 26 28 was being
12539000998014861558 gerund 14 16 was setting
12539000998014861558 gerund 30 32 was doing
12539000998014861558 gerund 83 85 be thinking
12539000998014861558 gerund 4 6 was thinking
12539000998014861558 gerund 32 34 been living
12539000998014861558 gerund 13 15 was delivering
12539000998014861558 gerund 68 70 was presenting
12539000998014861558 gerund 40 42 were trying
12539000998014861558 gerund 59 61 was 

12539000998014861558 gerund 29 31 was loitering
12539000998014861558 gerund 1 3 is muttering
all_en.txt
12539000998014861558 gerund 11 13 been thinking
12539000998014861558 gerund 4 6 been thinking
12539000998014861558 gerund 20 22 been paying
12539000998014861558 gerund 4 6 was pulling
12539000998014861558 gerund 20 22 was reminding
12539000998014861558 gerund 9 11 was dying
12539000998014861558 gerund 20 22 was breaking
12539000998014861558 gerund 2 4 were coming
12539000998014861558 gerund 1 3 is building
12539000998014861558 gerund 13 15 are sending
12539000998014861558 gerund 11 13 been reporting
12539000998014861558 gerund 31 33 is falling
12539000998014861558 gerund 2 4 was sheeting
12539000998014861558 gerund 12 14 was racing
12539000998014861558 gerund 14 16 were laughing
12539000998014861558 gerund 31 33 was sleeping
12539000998014861558 gerund 33 35 were starting
12539000998014861558 gerund 2 4 was quivering
12539000998014861558 gerund 3 5 be happening
12539000998014861558 g

...

12539000998014861558 gerund 4 6 was blooming
12539000998014861558 gerund 2 4 was hurrying
12539000998014861558 gerund 9 11 been watching
12539000998014861558 gerund 5 7 was happening
12539000998014861558 gerund 10 12 was disturbing
12539000998014861558 gerund 13 15 been playing
12539000998014861558 gerund 10 12 was going
12539000998014861558 gerund 9 11 was going
12539000998014861558 gerund 1 3 was wearing
12539000998014861558 gerund 2 4 were shaking
12539000998014861558 gerund 6 8 been standing
12539000998014861558 gerund 5 7 was going
12539000998014861558 gerund 8 10 were hanging
12539000998014861558 gerund 12 14 was going
12539000998014861558 gerund 5 7 was lingering
12539000998014861558 gerund 35 37 were flying
12539000998014861558 gerund 14 16 were treating
12539000998014861558 gerund 1 3 was lacking
12539000998014861558 gerund 3 5 was exclaiming
12539000998014861558 gerund 6 8 was going
12539000998014861558 gerund 2 4 was running
12539000998014861558 gerund 5 7 was forming
125390

12539000998014861558 gerund 1 3 was scooping
12539000998014861558 gerund 18 20 was beating
12539000998014861558 gerund 12 14 was wearing
12539000998014861558 gerund 2 4 was crossing
12539000998014861558 gerund 24 26 is saying
12539000998014861558 gerund 3 5 be crying
12539000998014861558 gerund 6 8 were sorting
12539000998014861558 gerund 3 5 was setting
12539000998014861558 gerund 24 26 were sleeping
12539000998014861558 gerund 3 5 been sorting
12539000998014861558 gerund 10 12 was pulling
12539000998014861558 gerund 18 20 were changing
12539000998014861558 gerund 9 11 were appearing
12539000998014861558 gerund 14 16 were looking
12539000998014861558 gerund 2 4 was fanning
12539000998014861558 gerund 25 27 were playing
12539000998014861558 gerund 6 8 was working
12539000998014861558 gerund 1 3 was wearing
12539000998014861558 gerund 9 11 were covering
12539000998014861558 gerund 31 33 been standing
12539000998014861558 gerund 38 40 was happening
12539000998014861558 gerund 8 10 be thi

12539000998014861558 gerund 110 112 were leaning
12539000998014861558 gerund 10 12 was going
12539000998014861558 gerund 1 3 was going
12539000998014861558 gerund 13 15 was going
12539000998014861558 gerund 27 29 was turning
12539000998014861558 gerund 34 36 were sitting
12539000998014861558 gerund 2 4 was going
12539000998014861558 gerund 6 8 was doing
12539000998014861558 gerund 43 45 was pacing
12539000998014861558 gerund 1 3 was smoking
12539000998014861558 gerund 6 8 were going
12539000998014861558 gerund 2 4 was saying
12539000998014861558 gerund 16 18 was going
12539000998014861558 gerund 1 3 was enjoying
12539000998014861558 gerund 8 10 was going
12539000998014861558 gerund 12 14 was supervising
12539000998014861558 gerund 4 6 is smoking
12539000998014861558 gerund 3 5 gets going
12539000998014861558 gerund 22 24 was going
12539000998014861558 gerund 24 26 were sitting
12539000998014861558 gerund 15 17 was handing
12539000998014861558 gerund 13 15 been making
125390009980148615

12539000998014861558 gerund 21 23 would fling
12539000998014861558 gerund 40 42 was graying
12539000998014861558 gerund 11 13 was leaning
12539000998014861558 gerund 38 40 am leaving
12539000998014861558 gerund 42 44 am leaving
12539000998014861558 gerund 3 5 were breaking
12539000998014861558 gerund 5 7 are kicking
12539000998014861558 gerund 8 10 be coming
12539000998014861558 gerund 10 12 was awaiting
12539000998014861558 gerund 23 25 was applying
12539000998014861558 gerund 51 53 was coming
12539000998014861558 gerund 10 12 were behaving
12539000998014861558 gerund 5 7 was becoming
12539000998014861558 gerund 3 5 was doing
12539000998014861558 gerund 16 18 were becoming
12539000998014861558 gerund 13 15 be reading
12539000998014861558 gerund 16 18 be becoming
12539000998014861558 gerund 5 7 was becoming
12539000998014861558 gerund 36 38 was referring
12539000998014861558 gerund 11 13 was earning
12539000998014861558 gerund 2 4 're changing
12539000998014861558 gerund 8 10 was tryin

12539000998014861558 gerund 24 26 is moving
12539000998014861558 gerund 2 4 is moving
12539000998014861558 gerund 16 18 was missing
12539000998014861558 gerund 7 9 're stepping
12539000998014861558 gerund 6 8 're wearing
12539000998014861558 gerund 10 12 are raging
12539000998014861558 gerund 9 11 been entering
12539000998014861558 gerund 2 4 is puzzling
12539000998014861558 gerund 3 5 is poisoning
12539000998014861558 gerund 14 16 was getting
12539000998014861558 gerund 2 4 're going
12539000998014861558 gerund 5 7 are yielding
12539000998014861558 gerund 10 12 was whispering
12539000998014861558 gerund 2 4 were thickening
12539000998014861558 gerund 1 3 're going
12539000998014861558 gerund 6 8 'm beginning
12539000998014861558 gerund 8 10 were groaning
12539000998014861558 gerund 13 15 was laughing
12539000998014861558 gerund 3 5 was stealing
12539000998014861558 gerund 1 3 'm going
12539000998014861558 gerund 16 18 's holding
12539000998014861558 gerund 3 5 was jumping
125390009980

In [14]:
#Fisher's exact: gerund (w/ aux)

print('gerund w/ aux')
print('e.g. were rolling')

#ru
oddsratio, pvalue = scipy.stats.fisher_exact([[733, 78750], [597, 78886]])
print('ru')
print(pvalue)

#pt
oddsratio, pvalue = scipy.stats.fisher_exact([[274, 34256], [259, 34270]])
print('pt')
print(pvalue)

#it
oddsratio, pvalue = scipy.stats.fisher_exact([[250, 36209], [274, 36185]])
print('it')
print(pvalue)

#es
oddsratio, pvalue = scipy.stats.fisher_exact([[369, 35320], [268, 35421]])
print('es')
print(pvalue)

#id
oddsratio, pvalue = scipy.stats.fisher_exact([[193, 20134], [153, 20174]])
print('id')
print(pvalue)

#de
oddsratio, pvalue = scipy.stats.fisher_exact([[366, 43977], [333, 44010]])
print('de')
print(pvalue)

#ko
oddsratio, pvalue = scipy.stats.fisher_exact([[1569, 146481], [1112, 146938]])
print('ko')
print(pvalue)

gerund w/ aux
e.g. were rolling
ru
0.00019899605642464914
pt
0.542722109388858
it
0.31326646200053404
es
6.674483125695618e-05
id
0.0350871769061252
de
0.22428328861832403
ko
7.447563050576268e-19


### 4.3 have
Russian expresses possession using a construction with the "be" verb. We wanted to see if this impacted the frequency with which "have" occurs (in the meaning of possession).

In [15]:
#have
pattern = [{}, {"DEP": "ROOT", "LEMMA": "have"}, {"LEMMA": {"NOT_IN": ["to"]}}]

matcher.add("have", None, pattern)
for filename in os.listdir(sourcefiledirectory):
    if filename.startswith("all"):
        
        f = open(filename, 'r')
        text = f.read()
        lines = sent_tokenize(text)
        outname = filename.replace('all', 'tmp_')
        with open(outname, 'w') as out:
            print(filename)
            for index,line in enumerate(lines):
                annotated_line = nlp(line)
                matches = matcher(annotated_line)
                for match_id, start, end in matches:
                    string_id = nlp.vocab.strings[match_id]  # Get string representation
                    span = annotated_line[start:end]  # The matched span
                    print(match_id, string_id, start, end, span.text)
                    out.write(str(match_id))
                    out.write("\n")
for filename in os.listdir(sourcefiledirectory):
    if filename.startswith("tmp_"):
        with open(filename, 'r') as f:
            outname = filename.replace('tmp_', 'have_')
            num_lines = 0
            with open(outname, 'w') as out:
                for line in f:
                    num_lines += 1
                print(filename)
                print(num_lines)
                out.write(str(num_lines))
matcher.remove("have")

all_ru.txt
14692702688101715474 have 6 9 n’t have enough
14692702688101715474 have 1 4 they hadn’t
14692702688101715474 have 2 5 n’t have too
14692702688101715474 have 3 6 inhabit have no
14692702688101715474 have 2 5 I had no
14692702688101715474 have 0 3 I had no
14692702688101715474 have 0 3 Farid had a
14692702688101715474 have 18 21 nearly had a
14692702688101715474 have 1 4 paramedic had no
14692702688101715474 have 0 3 I had no
14692702688101715474 have 2 5 you have for
14692702688101715474 have 1 4 I have a
14692702688101715474 have 15 18 n’t have any
14692702688101715474 have 10 13 I had no
14692702688101715474 have 1 4 bathroom had no
14692702688101715474 have 0 3 He had several
14692702688101715474 have 6 9 even have any
14692702688101715474 have 2 5 you have any
14692702688101715474 have 4 7 n’t have two
14692702688101715474 have 15 18 still hadn’t
14692702688101715474 have 3 6 even have a
14692702688101715474 have 6 9 would have plenty
14692702688101715474 have 15 18 you h

14692702688101715474 have 21 24 he had enough
14692702688101715474 have 2 5 ’ve had it
14692702688101715474 have 0 3 He had good
14692702688101715474 have 0 3 She had a
14692702688101715474 have 1 4 suddenly had the
14692702688101715474 have 1 4 I have a
14692702688101715474 have 1 4 half had its
14692702688101715474 have 0 3 I have a
14692702688101715474 have 15 18 girl has three
14692702688101715474 have 38 41 I have a
14692702688101715474 have 22 25 To have days
14692702688101715474 have 9 12 you have children
14692702688101715474 have 2 5 have had her
14692702688101715474 have 22 25 Yasha had a
14692702688101715474 have 4 7 you have us
14692702688101715474 have 3 6 I have you
14692702688101715474 have 3 6 n’t have me
14692702688101715474 have 0 3 He had a
14692702688101715474 have 1 4 already had the
14692702688101715474 have 1 4 always had difficulty
14692702688101715474 have 6 9 , had no
14692702688101715474 have 3 6 , have a
14692702688101715474 have 12 15 two have different
146

14692702688101715474 have 1 4 It has heating
14692702688101715474 have 8 11 scoreboard had us
14692702688101715474 have 30 33 have had a
14692702688101715474 have 8 11 had had the
14692702688101715474 have 4 7 n’t have a
14692702688101715474 have 0 3 Turner had warehouse
14692702688101715474 have 1 4 boy had stones
14692702688101715474 have 1 4 story had complicated
14692702688101715474 have 2 5 n’t had the
14692702688101715474 have 0 3 He had two
14692702688101715474 have 10 13 one had the
14692702688101715474 have 3 6 he had a
14692702688101715474 have 7 10 , had a
14692702688101715474 have 1 4 father had hold
14692702688101715474 have 0 3 She has a
14692702688101715474 have 0 3 Aidan has a
14692702688101715474 have 0 3 He has the
14692702688101715474 have 0 3 Declan has a
14692702688101715474 have 8 11 n’t have a
14692702688101715474 have 1 4 you have even
14692702688101715474 have 10 13 ’ll have one
14692702688101715474 have 9 12 n’t have one
14692702688101715474 have 1 4 ’ll have 

14692702688101715474 have 10 13 n’t have the
14692702688101715474 have 0 3 He had twice
14692702688101715474 have 2 5 n’t have a
14692702688101715474 have 37 40 , had an
14692702688101715474 have 1 4 he have a
14692702688101715474 have 1 4 they have a
14692702688101715474 have 1 4 they have the
14692702688101715474 have 1 4 Bev had it
14692702688101715474 have 3 6 would have occasion
14692702688101715474 have 6 9 still had a
14692702688101715474 have 1 4 it hadn’t
14692702688101715474 have 3 6 could have it
14692702688101715474 have 5 8 she had no
14692702688101715474 have 1 4 had had Theodore
14692702688101715474 have 12 15 I haven’t
14692702688101715474 have 1 4 I have some
14692702688101715474 have 10 13 You have wine
14692702688101715474 have 3 6 ’ll have friends
14692702688101715474 have 1 4 even have some
14692702688101715474 have 9 12 You have friends
14692702688101715474 have 6 9 I have a
14692702688101715474 have 19 22 I have my
14692702688101715474 have 1 4 they had.
14692702

14692702688101715474 have 11 14 I’ve

14692702688101715474 have 52 55 not have an
14692702688101715474 have 2 5 n’t have any
14692702688101715474 have 0 3 He has a
14692702688101715474 have 14 17 
haven’t
14692702688101715474 have 78 81 country has its
all_de.txt
14692702688101715474 have 4 7 , have the
14692702688101715474 have 0 3 He had—
14692702688101715474 have 19 22 he had great
14692702688101715474 have 1 4 had had no
14692702688101715474 have 0 3 He had the
14692702688101715474 have 0 3 He had a
14692702688101715474 have 7 10 could have if
14692702688101715474 have 1 4 even had company
14692702688101715474 have 0 3 He had no
14692702688101715474 have 0 3 He had ten
14692702688101715474 have 0 3 He had some
14692702688101715474 have 21 24 even had the
14692702688101715474 have 5 8 he had not
14692702688101715474 have 0 3 Aschenbach had difficulty
14692702688101715474 have 1 4 then had three
14692702688101715474 have 1 4 had had ample
14692702688101715474 have 0 3 You have no
146

14692702688101715474 have 19 22 , haven’t
14692702688101715474 have 2 5 I have another
14692702688101715474 have 26 29 he had the
14692702688101715474 have 1 4 all have acute
14692702688101715474 have 6 9 it has a
14692702688101715474 have 21 24 also has its
14692702688101715474 have 14 17 soils have in
14692702688101715474 have 1 4 house has its
14692702688101715474 have 2 5 n’t have the
14692702688101715474 have 21 24 , had the
14692702688101715474 have 0 3 It has colonnades
14692702688101715474 have 11 14 always has this
14692702688101715474 have 2 5 always have fond
14692702688101715474 have 2 5 not have him
14692702688101715474 have 0 3 We have letters
14692702688101715474 have 8 11 he has visions
14692702688101715474 have 2 5 releases had titles
14692702688101715474 have 4 7 they have its
14692702688101715474 have 9 12 we had a
14692702688101715474 have 0 3 I have my
14692702688101715474 have 1 4 ’d have a
14692702688101715474 have 3 6 they had nothing
14692702688101715474 have 2

14692702688101715474 have 7 10 , had no
14692702688101715474 have 5 8  had them
14692702688101715474 have 3 6 children had 
14692702688101715474 have 3 6 dwarf had 
14692702688101715474 have 4 7 kids had it
14692702688101715474 have 2 5 would have 
14692702688101715474 have 2 5 ho had an
14692702688101715474 have 0 3 They have no
14692702688101715474 have 3 6 inspectors have 
14692702688101715474 have 7 10 father had them
14692702688101715474 have 1 4  had no
14692702688101715474 have 18 21 -have s
14692702688101715474 have 3 6 n’t have anything
14692702688101715474 have 0 3 They have no
14692702688101715474 have 1 4 ’ve had enough
14692702688101715474 have 0 3 He has pretty
14692702688101715474 have 3 6 I have a
14692702688101715474 have 12 15 -have so
14692702688101715474 have 22 25 have had too
14692702688101715474 have 0 3 It had the
14692702688101715474 have 2 5 ho had terrible
14692702688101715474 have 1 4 they had only
14692702688101715474 have 2 5 really having wine
14692702688

14692702688101715474 have 4 7 you have 
14692702688101715474 have 2 5 not have the
14692702688101715474 have 50 53 “Hadn’t
14692702688101715474 have 9 12 would have 
14692702688101715474 have 2 5 mistress had no
14692702688101715474 have 0 3 She had no
14692702688101715474 have 13 16 would have a
14692702688101715474 have 20 23 have had 
14692702688101715474 have 2 5 you had supper
14692702688101715474 have 1 4 probably had no
14692702688101715474 have 29 32 you have fine
14692702688101715474 have 1 4 I had a
14692702688101715474 have 2 5 , haven’t
14692702688101715474 have 1 4 always had the
14692702688101715474 have 2 5 woman had gall
14692702688101715474 have 1 4 father had an
14692702688101715474 have 2 5 woman had a
14692702688101715474 have 2 5 can have something
14692702688101715474 have 0 3 Nana had the
14692702688101715474 have 9 12 I have 
14692702688101715474 have 23 26 he have his
14692702688101715474 have 22 25 not had the
14692702688101715474 have 0 3 I haven’t
1469270268

14692702688101715474 have 1 4 I've three
14692702688101715474 have 0 3 They had a
14692702688101715474 have 1 4 still have it
14692702688101715474 have 9 12 it has an
14692702688101715474 have 22 25 sometimes have the
14692702688101715474 have 2 5 n't had another
14692702688101715474 have 0 3 She had small
14692702688101715474 have 0 3 I have no
14692702688101715474 have 0 3 She had a
14692702688101715474 have 17 20 , had the
14692702688101715474 have 0 3 I had a
all_id.txt
14692702688101715474 have 2 5 he has a
14692702688101715474 have 52 55 I had no
14692702688101715474 have 14 17 , has more
14692702688101715474 have 0 3 He has fifteen
14692702688101715474 have 18 21 will have a
14692702688101715474 have 68 71 we had more
14692702688101715474 have 0 3 He had three
14692702688101715474 have 22 25 would have their
14692702688101715474 have 0 3 Word had it
14692702688101715474 have 24 27 you have a
14692702688101715474 have 1 4 I had no
14692702688101715474 have 0 3 I had no
1469270268

In [16]:
#have

#ru
print('have (verb)')
oddsratio, pvalue = scipy.stats.fisher_exact([[300, 158665], [305, 158660]])
print('ru')#
print(pvalue)

#pt
oddsratio, pvalue = scipy.stats.fisher_exact([[91, 68968], [133, 68926]])
print('pt')
print(pvalue)

#it
oddsratio, pvalue = scipy.stats.fisher_exact([[106, 72811], [140, 72777]])
print('it')
print(pvalue)

#es
oddsratio, pvalue = scipy.stats.fisher_exact([[100, 71278], [137, 71241]])
print('es')
print(pvalue)

#id
oddsratio, pvalue = scipy.stats.fisher_exact([[80, 40574], [78, 40576]])
print('id')
print(pvalue)

#de
oddsratio, pvalue = scipy.stats.fisher_exact([[112, 88573], [170, 88515]])
print('de')
print(pvalue)

#ko
oddsratio, pvalue = scipy.stats.fisher_exact([[447, 295652], [568, 295531]])
print('ko')
print(pvalue)

have (verb)
ru
0.8707103329136558
pt
0.005989501249826898
it
0.03501068055990829
es
0.01907329882433328
id
0.9365624031496083
de
0.0006551136288865059
ko
0.0001607044309734734


### 4.4 it's/that's
van Halteren (2008) satates that "it's" and "that's" are less frequent in translated texts in the Europarl corpus, so we wanted to see if we could find the same effect in these literary translations.

Problem: apostrophes are characters used when writing Python code. In theory they should be escapable... but none of my attempts to escape them succeeded. So I opened the corpora in a text editor and did a case-insensitive word count for "it's" and "that's" and added those numbers together, then put them in Excel for finding the values for Fisher's exact.


In [17]:
#that's/it's

#ru
print('that\'s/it\'s')
oddsratio, pvalue = scipy.stats.fisher_exact([[63, 158902], [10, 158955]])
print('ru')#
print(pvalue)

#pt
oddsratio, pvalue = scipy.stats.fisher_exact([[0, 69059], [4, 69055]])
print('pt')
print(pvalue)

#it
oddsratio, pvalue = scipy.stats.fisher_exact([[0, 72917], [5, 72912]])
print('it')
print(pvalue)

#es
oddsratio, pvalue = scipy.stats.fisher_exact([[14, 71364], [5, 71373]])
print('es')
print(pvalue)

#id
oddsratio, pvalue = scipy.stats.fisher_exact([[38, 40616], [3, 40651]])
print('id')
print(pvalue)

#de
oddsratio, pvalue = scipy.stats.fisher_exact([[31, 88654], [6, 88679]])
print('de')
print(pvalue)

#ko
oddsratio, pvalue = scipy.stats.fisher_exact([[394, 295705], [19, 19]])
print('ko')
print(pvalue)

that's/it's
ru
1.5468303362931497e-10
pt
0.12499456978784572
it
0.06249571431829425
es
0.06355071507093797
id
1.0402412996462495e-08
de
4.1186684488466865e-05
ko
1.2597138141418624e-44


### 4.5 Past participles
Russian use of past participles differs from English, so we wanted to see if that had an impact on how past participles appear in the English translations.

In [18]:
#past participle
pattern = [{"DEP": "aux"}, {"TAG": "VBN"}, {}]

matcher.add("pastpart", None, pattern)
for filename in os.listdir(sourcefiledirectory):
    if filename.startswith("all"):
        
        f = open(filename, 'r')
        text = f.read()
        lines = sent_tokenize(text)
        outname = filename.replace('all', 'tmp_')
        with open(outname, 'w') as out:
            print(filename)
            for index,line in enumerate(lines):
                annotated_line = nlp(line)
                matches = matcher(annotated_line)
                for match_id, start, end in matches:
                    string_id = nlp.vocab.strings[match_id]  # Get string representation
                    span = annotated_line[start:end]  # The matched span
                    print(match_id, string_id, start, end, span.text)
                    out.write(str(match_id))
                    out.write("\n")
for filename in os.listdir(sourcefiledirectory):
    if filename.startswith("tmp_"):
        with open(filename, 'r') as f:
            outname = filename.replace('tmp_', 'pastpart_')
            num_lines = 0
            with open(outname, 'w') as out:
                for line in f:
                    num_lines += 1
                print(filename)
                print(num_lines)
                out.write(str(num_lines))
matcher.remove("pastpart")

all_ru.txt
4266497899917444067 pastpart 23 26 had pushed together
4266497899917444067 pastpart 10 13 had taken a
4266497899917444067 pastpart 2 5 had given way
4266497899917444067 pastpart 16 19 had gone out
4266497899917444067 pastpart 1 4 had lost part
4266497899917444067 pastpart 5 8 had been severely
4266497899917444067 pastpart 1 4 had received a
4266497899917444067 pastpart 36 39 had spelled out
4266497899917444067 pastpart 2 5 had tightened the
4266497899917444067 pastpart 14 17 have stopped the
4266497899917444067 pastpart 1 4 had dealt with
4266497899917444067 pastpart 1 4 had taken us
4266497899917444067 pastpart 1 4 had chosen this
4266497899917444067 pastpart 4 7 had been at
4266497899917444067 pastpart 18 21 had died.
4266497899917444067 pastpart 8 11 had become “
4266497899917444067 pastpart 20 23 had carried him
4266497899917444067 pastpart 14 17 have expected.
4266497899917444067 pastpart 4 7 had been watching
4266497899917444067 pastpart 1 4 had removed the
42664978999

4266497899917444067 pastpart 10 13 have grown sharper
4266497899917444067 pastpart 3 6 has been turned
4266497899917444067 pastpart 1 4 has matured in
4266497899917444067 pastpart 13 16 had dealt so
4266497899917444067 pastpart 20 23 has been illegally
4266497899917444067 pastpart 3 6 had been wrecked
4266497899917444067 pastpart 11 14 had awakened the
4266497899917444067 pastpart 11 14 had housed two
4266497899917444067 pastpart 3 6 had suffered for
4266497899917444067 pastpart 7 10 have paled at
4266497899917444067 pastpart 7 10 have been impossible
4266497899917444067 pastpart 27 30 had held the
4266497899917444067 pastpart 42 45 had come upon
4266497899917444067 pastpart 29 32 had stopped by
4266497899917444067 pastpart 2 5 have been in
4266497899917444067 pastpart 1 4 have been eaten
4266497899917444067 pastpart 11 14 had made nests
4266497899917444067 pastpart 18 21 had grown to
4266497899917444067 pastpart 1 4 had gained so
4266497899917444067 pastpart 9 12 had vanished—
4266497

4266497899917444067 pastpart 34 37 have been just
4266497899917444067 pastpart 42 45 have been at
4266497899917444067 pastpart 4 7 had covered all
4266497899917444067 pastpart 16 19 have been a
4266497899917444067 pastpart 9 12 had gone missing
4266497899917444067 pastpart 10 13 had arranged for
4266497899917444067 pastpart 31 34 had been buried
4266497899917444067 pastpart 8 11 had gotten along
4266497899917444067 pastpart 28 31 had dressed and
4266497899917444067 pastpart 40 43 had forbidden her
4266497899917444067 pastpart 21 24 had seen a
4266497899917444067 pastpart 36 39 had changed.
4266497899917444067 pastpart 10 13 had put Tamara
4266497899917444067 pastpart 45 48 had been finished
4266497899917444067 pastpart 51 54 have dissolved,
4266497899917444067 pastpart 63 66 have traveled all
4266497899917444067 pastpart 5 8 having decided he
4266497899917444067 pastpart 3 6 had offered several
4266497899917444067 pastpart 3 6 had grown fond
4266497899917444067 pastpart 9 12 had begun.

4266497899917444067 pastpart 8 11 had gotten used
4266497899917444067 pastpart 2 5 had been prompted
4266497899917444067 pastpart 4 7 had frightened him
4266497899917444067 pastpart 11 14 had been in
4266497899917444067 pastpart 1 4 had been nicknamed
4266497899917444067 pastpart 9 12 had grown to
4266497899917444067 pastpart 2 5 have divorced,
4266497899917444067 pastpart 11 14 'd frightened her
4266497899917444067 pastpart 18 21 had earned his
4266497899917444067 pastpart 12 15 had striven for
4266497899917444067 pastpart 26 29 had been ready
4266497899917444067 pastpart 3 6 had devoured her
4266497899917444067 pastpart 4 7 have cared less
4266497899917444067 pastpart 8 11 had hit whom
4266497899917444067 pastpart 32 35 have shared it
4266497899917444067 pastpart 2 5 have tarnished her
4266497899917444067 pastpart 64 67 had ended up
4266497899917444067 pastpart 3 6 have kicked the
4266497899917444067 pastpart 23 26 had grown tired
4266497899917444067 pastpart 3 6 had been an
42664978

4266497899917444067 pastpart 26 29 had been remodeled
4266497899917444067 pastpart 9 12 had built a
4266497899917444067 pastpart 36 39 had built in
4266497899917444067 pastpart 4 7 had rented out
4266497899917444067 pastpart 29 32 had gone for
4266497899917444067 pastpart 2 5 had been taken
4266497899917444067 pastpart 6 9 had reached draft
4266497899917444067 pastpart 2 5 had seen their
4266497899917444067 pastpart 2 5 had brought firewood
4266497899917444067 pastpart 16 19 have slept poorly
4266497899917444067 pastpart 4 7 had stashed away
4266497899917444067 pastpart 9 12 has come into
4266497899917444067 pastpart 5 8 have seen a
4266497899917444067 pastpart 5 8 had gone to
4266497899917444067 pastpart 10 13 had said then
4266497899917444067 pastpart 2 5 have called you
4266497899917444067 pastpart 10 13 had started to
4266497899917444067 pastpart 4 7 had passed since
4266497899917444067 pastpart 1 4 had happened,
4266497899917444067 pastpart 1 4 have left the
4266497899917444067 pa

...

4266497899917444067 pastpart 10 13 had been set
4266497899917444067 pastpart 14 17 had fired off
4266497899917444067 pastpart 8 11 had dropped his
4266497899917444067 pastpart 8 11 had looked at
4266497899917444067 pastpart 11 14 had fallen down
all_es.txt
4266497899917444067 pastpart 30 33 have imagined—
4266497899917444067 pastpart 48 51 had given me
4266497899917444067 pastpart 6 9 had arrived,
4266497899917444067 pastpart 12 15 have been listening
4266497899917444067 pastpart 3 6 had been sick
4266497899917444067 pastpart 25 28 had found her
4266497899917444067 pastpart 16 19 had seemed disproportionate
4266497899917444067 pastpart 1 4 had seen her
4266497899917444067 pastpart 1 4 had told me
4266497899917444067 pastpart 31 34 have gone—
4266497899917444067 pastpart 2 5 had tried to
4266497899917444067 pastpart 29 32 had landed the
4266497899917444067 pastpart 11 14 have been able
4266497899917444067 pastpart 35 38 had referred to
4266497899917444067 pastpart 19 22 had come in
4266

4266497899917444067 pastpart 17 20 have been more
4266497899917444067 pastpart 20 23 had brushed forward
4266497899917444067 pastpart 20 23 have seen a
4266497899917444067 pastpart 6 9 had said.
4266497899917444067 pastpart 38 41 have been the
4266497899917444067 pastpart 9 12 having checked the
4266497899917444067 pastpart 36 39 had left my
4266497899917444067 pastpart 6 9 had reached his
4266497899917444067 pastpart 9 12 had seen his
4266497899917444067 pastpart 2 5 have been at
4266497899917444067 pastpart 33 36 had observed on
4266497899917444067 pastpart 8 11 had led me
4266497899917444067 pastpart 28 31 have continued to
4266497899917444067 pastpart 21 24 had given me
4266497899917444067 pastpart 2 5 had suspected,
4266497899917444067 pastpart 36 39 had seen from
4266497899917444067 pastpart 19 22 had said without
4266497899917444067 pastpart 11 14 have been the
4266497899917444067 pastpart 11 14 had taken—
4266497899917444067 pastpart 1 4 had stretched out
4266497899917444067 pa

4266497899917444067 pastpart 3 6 had stopped and
4266497899917444067 pastpart 181 184 have decked me
4266497899917444067 pastpart 16 19 have wound up
4266497899917444067 pastpart 10 13 had put together
4266497899917444067 pastpart 7 10 have warned them
4266497899917444067 pastpart 22 25 have scared them
4266497899917444067 pastpart 4 7 has forgotten to
4266497899917444067 pastpart 8 11 had been she
4266497899917444067 pastpart 16 19 had abandoned her
4266497899917444067 pastpart 3 6 have suffered with
4266497899917444067 pastpart 20 23 had kept to
4266497899917444067 pastpart 23 26 has fabricated toward
4266497899917444067 pastpart 15 18 had married him
4266497899917444067 pastpart 4 7 has retreated!
4266497899917444067 pastpart 1 4 had departed quietly
4266497899917444067 pastpart 2 5 had been right
4266497899917444067 pastpart 7 10 had replied childishly
4266497899917444067 pastpart 2 5 had refused to
4266497899917444067 pastpart 15 18 had discovered without
4266497899917444067 pastp

4266497899917444067 pastpart 1 4 had been walking
4266497899917444067 pastpart 14 17 had got to
4266497899917444067 pastpart 1 4 had been dropped
4266497899917444067 pastpart 14 17 had been the
4266497899917444067 pastpart 18 21 had abandoned her
4266497899917444067 pastpart 18 21 had begun the
4266497899917444067 pastpart 4 7 had shrunk to
4266497899917444067 pastpart 1 4 'd jotted down
4266497899917444067 pastpart 9 12 had managed to
4266497899917444067 pastpart 27 30 had caught the
4266497899917444067 pastpart 40 43 has blocked out
4266497899917444067 pastpart 16 19 'd forgotten.
4266497899917444067 pastpart 27 30 had stopped playing
4266497899917444067 pastpart 13 16 had chosen to
all_id.txt
4266497899917444067 pastpart 4 7 had grasped the
4266497899917444067 pastpart 11 14 had heard,
4266497899917444067 pastpart 14 17 had said.
4266497899917444067 pastpart 10 13 had understood her
4266497899917444067 pastpart 9 12 had taken our
4266497899917444067 pastpart 18 21 had begun to
42664

4266497899917444067 pastpart 15 18 had been caught
4266497899917444067 pastpart 7 10 had made the
4266497899917444067 pastpart 3 6 has become mad
4266497899917444067 pastpart 4 7 had been secretly
4266497899917444067 pastpart 5 8 had ended with
4266497899917444067 pastpart 8 11 had been completely
4266497899917444067 pastpart 5 8 had said that
4266497899917444067 pastpart 8 11 've eaten meat
4266497899917444067 pastpart 5 8 had cared for
4266497899917444067 pastpart 14 17 had curled his
4266497899917444067 pastpart 19 22 had returned in
4266497899917444067 pastpart 22 25 had been born
4266497899917444067 pastpart 2 5 have been her
4266497899917444067 pastpart 3 6 had been able
4266497899917444067 pastpart 16 19 had concealed her
4266497899917444067 pastpart 3 6 have fulfilled his
4266497899917444067 pastpart 10 13 had been sealed
4266497899917444067 pastpart 19 22 had oozed from
4266497899917444067 pastpart 52 55 have forgotten about
4266497899917444067 pastpart 5 8 had possessed me
42

In [19]:
#Past participle
#ru
print('past participle')
print('e.g. had been wheeling, had killed')
oddsratio, pvalue = scipy.stats.fisher_exact([[1071, 78412], [965, 78518]])
print('ru')#
print(pvalue)

#pt
oddsratio, pvalue = scipy.stats.fisher_exact([[574, 33956], [419, 34110]])
print('pt')
print(pvalue)

#it
oddsratio, pvalue = scipy.stats.fisher_exact([[505, 35954], [442, 36016]])
print('it')
print(pvalue)

#es
oddsratio, pvalue = scipy.stats.fisher_exact([[510, 35179], [433, 35256]])
print('es')
print(pvalue)

#id
oddsratio, pvalue = scipy.stats.fisher_exact([[313, 20014], [247, 20080]])
print('id')
print(pvalue)

#de
oddsratio, pvalue = scipy.stats.fisher_exact([[744, 43599], [538, 43804]])
print('de')
print(pvalue)

#ko
oddsratio, pvalue = scipy.stats.fisher_exact([[2597, 145453], [1797, 146253]])
print('ko')
print(pvalue)

past participle
e.g. had been wheeling, had killed
ru
0.019155668341648627
pt
8.140612964140166e-07
it
0.04251100487668476
es
0.012683607841963037
id
0.005630776939206904
de
7.50804845263062e-09
ko
4.112522352487317e-34


### 4.6 Some
We thought there might be some difference in the frequency of "some" in English for translations of Russian, because there are multiple words that could be translated that way.

In [20]:
#"some"
pattern = [{"POS": "DET", "LOWER": "some"}]

matcher.add("SOME", None, pattern)
for filename in os.listdir(sourcefiledirectory):
    if filename.startswith("all"):
        
        f = open(filename, 'r')
        text = f.read()
        lines = sent_tokenize(text)
        outname = filename.replace('all', 'tmp_')
        with open(outname, 'w') as out:
            print(filename)
            for index,line in enumerate(lines):
                annotated_line = nlp(line)
                matches = matcher(annotated_line)
                for match_id, start, end in matches:
                    string_id = nlp.vocab.strings[match_id]  # Get string representation
                    span = annotated_line[start:end]  # The matched span
                    print(match_id, string_id, start, end, span.text)
                    out.write(str(match_id))
                    out.write("\n")
for filename in os.listdir(sourcefiledirectory):
    if filename.startswith("tmp_"):
        with open(filename, 'r') as f:
            outname = filename.replace('tmp_', 'DET_some')
            num_lines = 0
            with open(outname, 'w') as out:
                for line in f:
                    num_lines += 1
                print(filename)
                print(num_lines)
                out.write(str(num_lines))
matcher.remove("SOME")

all_ru.txt
15016112045944751253 SOME 20 21 some
15016112045944751253 SOME 14 15 some
15016112045944751253 SOME 33 34 some
15016112045944751253 SOME 12 13 some
15016112045944751253 SOME 28 29 some
15016112045944751253 SOME 17 18 some
15016112045944751253 SOME 0 1 Some
15016112045944751253 SOME 17 18 some
15016112045944751253 SOME 5 6 some
15016112045944751253 SOME 7 8 some
15016112045944751253 SOME 19 20 some
15016112045944751253 SOME 4 5 some
15016112045944751253 SOME 8 9 some
15016112045944751253 SOME 10 11 some
15016112045944751253 SOME 1 2 some
15016112045944751253 SOME 11 12 some
15016112045944751253 SOME 5 6 some
15016112045944751253 SOME 12 13 some
15016112045944751253 SOME 18 19 some
15016112045944751253 SOME 16 17 some
15016112045944751253 SOME 5 6 some
15016112045944751253 SOME 0 1 Some
15016112045944751253 SOME 12 13 some
15016112045944751253 SOME 35 36 some
15016112045944751253 SOME 4 5 some
15016112045944751253 SOME 2 3 some
15016112045944751253 SOME 4 5 some
15016112045944

15016112045944751253 SOME 112 113 some
15016112045944751253 SOME 27 28 some
15016112045944751253 SOME 4 5 some
15016112045944751253 SOME 0 1 Some
15016112045944751253 SOME 22 23 some
15016112045944751253 SOME 13 14 some
15016112045944751253 SOME 17 18 some
15016112045944751253 SOME 25 26 some
15016112045944751253 SOME 5 6 some
15016112045944751253 SOME 11 12 some
15016112045944751253 SOME 9 10 some
15016112045944751253 SOME 4 5 some
15016112045944751253 SOME 42 43 some
15016112045944751253 SOME 8 9 some
15016112045944751253 SOME 46 47 some
15016112045944751253 SOME 1 2 some
15016112045944751253 SOME 14 15 some
15016112045944751253 SOME 1 2 Some
15016112045944751253 SOME 0 1 Some
15016112045944751253 SOME 9 10 some
15016112045944751253 SOME 26 27 some
15016112045944751253 SOME 4 5 some
15016112045944751253 SOME 19 20 some
15016112045944751253 SOME 2 3 some
15016112045944751253 SOME 8 9 some
15016112045944751253 SOME 16 17 some
15016112045944751253 SOME 24 25 some
15016112045944751253 SO

15016112045944751253 SOME 31 32 some
15016112045944751253 SOME 2 3 some
15016112045944751253 SOME 7 8 some
15016112045944751253 SOME 15 16 some
15016112045944751253 SOME 4 5 some
15016112045944751253 SOME 16 17 some
15016112045944751253 SOME 15 16 some
15016112045944751253 SOME 6 7 some
15016112045944751253 SOME 15 16 some
15016112045944751253 SOME 20 21 some
15016112045944751253 SOME 11 12 some
15016112045944751253 SOME 6 7 some
15016112045944751253 SOME 10 11 some
15016112045944751253 SOME 31 32 some
15016112045944751253 SOME 0 1 Some
15016112045944751253 SOME 11 12 some
15016112045944751253 SOME 18 19 some
15016112045944751253 SOME 31 32 some
15016112045944751253 SOME 36 37 some
15016112045944751253 SOME 14 15 some
15016112045944751253 SOME 9 10 some
15016112045944751253 SOME 5 6 some
15016112045944751253 SOME 2 3 some
15016112045944751253 SOME 1 2 some
15016112045944751253 SOME 7 8 some
15016112045944751253 SOME 2 3 some
15016112045944751253 SOME 5 6 some
15016112045944751253 SOME 

15016112045944751253 SOME 0 1 Some
15016112045944751253 SOME 22 23 some
15016112045944751253 SOME 35 36 some
15016112045944751253 SOME 23 24 some
15016112045944751253 SOME 12 13 some
15016112045944751253 SOME 56 57 some
15016112045944751253 SOME 19 20 some
15016112045944751253 SOME 33 34 some
15016112045944751253 SOME 8 9 some
15016112045944751253 SOME 27 28 some
15016112045944751253 SOME 30 31 some
15016112045944751253 SOME 31 32 some
15016112045944751253 SOME 12 13 some
15016112045944751253 SOME 12 13 some
15016112045944751253 SOME 10 11 some
15016112045944751253 SOME 0 1 Some
15016112045944751253 SOME 15 16 some
15016112045944751253 SOME 48 49 some
15016112045944751253 SOME 5 6 some
15016112045944751253 SOME 26 27 some
15016112045944751253 SOME 12 13 some
15016112045944751253 SOME 20 21 some
15016112045944751253 SOME 21 22 some
15016112045944751253 SOME 25 26 some
15016112045944751253 SOME 5 6 some
15016112045944751253 SOME 38 39 some
15016112045944751253 SOME 34 35 some
15016112045

15016112045944751253 SOME 2 3 some
15016112045944751253 SOME 4 5 some
15016112045944751253 SOME 3 4 some
15016112045944751253 SOME 2 3 some
15016112045944751253 SOME 5 6 some
15016112045944751253 SOME 4 5 some
15016112045944751253 SOME 2 3 some
15016112045944751253 SOME 10 11 some
15016112045944751253 SOME 3 4 some
15016112045944751253 SOME 9 10 some
15016112045944751253 SOME 6 7 some
15016112045944751253 SOME 5 6 some
15016112045944751253 SOME 17 18 some
15016112045944751253 SOME 7 8 some
15016112045944751253 SOME 0 1 Some
15016112045944751253 SOME 9 10 some
15016112045944751253 SOME 16 17 some
15016112045944751253 SOME 58 59 some
15016112045944751253 SOME 29 30 some
15016112045944751253 SOME 3 4 some
15016112045944751253 SOME 23 24 some
15016112045944751253 SOME 90 91 some
15016112045944751253 SOME 3 4 some
15016112045944751253 SOME 12 13 some
15016112045944751253 SOME 19 20 some
15016112045944751253 SOME 5 6 some
15016112045944751253 SOME 17 18 some
15016112045944751253 SOME 34 35 s

15016112045944751253 SOME 21 22 some
15016112045944751253 SOME 0 1 Some
15016112045944751253 SOME 23 24 some
15016112045944751253 SOME 11 12 some
15016112045944751253 SOME 24 25 some
15016112045944751253 SOME 2 3 some
15016112045944751253 SOME 10 11 some
15016112045944751253 SOME 8 9 some
15016112045944751253 SOME 1 2 some
15016112045944751253 SOME 10 11 some
15016112045944751253 SOME 18 19 some
15016112045944751253 SOME 9 10 some
15016112045944751253 SOME 4 5 some
15016112045944751253 SOME 2 3 some
15016112045944751253 SOME 14 15 some
15016112045944751253 SOME 1 2 some
15016112045944751253 SOME 19 20 some
15016112045944751253 SOME 12 13 some
15016112045944751253 SOME 2 3 some
15016112045944751253 SOME 4 5 some
15016112045944751253 SOME 28 29 some
15016112045944751253 SOME 2 3 some
15016112045944751253 SOME 19 20 some
15016112045944751253 SOME 2 3 some
15016112045944751253 SOME 2 3 some
15016112045944751253 SOME 12 13 some
15016112045944751253 SOME 17 18 some
15016112045944751253 SOME 

15016112045944751253 SOME 10 11 some
15016112045944751253 SOME 20 21 some
15016112045944751253 SOME 14 15 some
15016112045944751253 SOME 29 30 some
15016112045944751253 SOME 65 66 some
15016112045944751253 SOME 10 11 some
15016112045944751253 SOME 13 14 some
15016112045944751253 SOME 6 7 some
15016112045944751253 SOME 22 23 some
15016112045944751253 SOME 4 5 some
15016112045944751253 SOME 15 16 some
15016112045944751253 SOME 6 7 some
15016112045944751253 SOME 20 21 some
15016112045944751253 SOME 3 4 some
15016112045944751253 SOME 14 15 some
15016112045944751253 SOME 20 21 some
15016112045944751253 SOME 29 30 some
15016112045944751253 SOME 7 8 some
15016112045944751253 SOME 8 9 some
15016112045944751253 SOME 29 30 some
15016112045944751253 SOME 2 3 some
15016112045944751253 SOME 2 3 some
15016112045944751253 SOME 1 2 some
15016112045944751253 SOME 2 3 some
15016112045944751253 SOME 12 13 some
15016112045944751253 SOME 9 10 some
15016112045944751253 SOME 15 16 some
15016112045944751253 S

In [21]:
#some
print('some')

#ru
oddsratio, pvalue = scipy.stats.fisher_exact([[258, 158707], [209, 158756]])
print('ru')
print(pvalue)

#pt
oddsratio, pvalue = scipy.stats.fisher_exact([[113, 68946], [91, 68968]])
print('pt')
print(pvalue)

#it
oddsratio, pvalue = scipy.stats.fisher_exact([[117, 72800], [96, 72821]])
print('it')
print(pvalue)

#es
oddsratio, pvalue = scipy.stats.fisher_exact([[119, 71259], [94, 71284]])
print('es')
print(pvalue)

#id
oddsratio, pvalue = scipy.stats.fisher_exact([[49, 40605], [55, 40599]])
print('id')
print(pvalue)

#de
oddsratio, pvalue = scipy.stats.fisher_exact([[124, 88561], [121, 88564]])
print('de')
print(pvalue)

#ko
oddsratio, pvalue = scipy.stats.fisher_exact([[519, 295580], [403, 295696]])
print('ko')
print(pvalue)

some
ru
0.02612342595981299
pt
0.14099968857951017
it
0.17011048442477092
es
0.09960340407369353
id
0.6239209429573161
de
0.8982908387087031
ko
0.0001477235128266448


### 4.7 'that'
Olohan (2001) states that translated texts have a higher frequency of "that" as a complementizer after reporting verbs (e.g. 'said that'). We looked at it (as *'that'-ADP* for the part-of-speech marker used in Spacy for that construction), as well as the use of "that" as a determiner.

#### 4.7.1 'That' ADP

In [22]:
#ThatADP - with verb beforehand

pattern = [{"POS": "VERB"},{"LEMMA": "that", "POS": "ADP"},{}]
matcher.add("thatADP", None, pattern)
for filename in os.listdir(sourcefiledirectory):
    if filename.startswith("all"):
        
        f = open(filename, 'r')
        text = f.read()
    
        
        
        
        lines = sent_tokenize(text)
        outname = filename.replace('all', 'tmp_')
        with open(outname, 'w') as out:
            for index,line in enumerate(lines):
                annotated_line = nlp(line)
                matches = matcher(annotated_line)
                for match_id, start, end in matches:
                    string_id = nlp.vocab.strings[match_id]  # Get string representation
                    span = annotated_line[start:end]  # The matched span
                    print(match_id, string_id, start, end, span.text)
                    out.write(str(match_id))
                    out.write("\n")
for filename in os.listdir(sourcefiledirectory):
    if filename.startswith("tmp_"):
        with open(filename, 'r') as f:
            outname = filename.replace('tmp_', 'thatVERB_ADP_')
            num_lines = 0
            with open(outname, 'w') as out:
                for line in f:
                    num_lines += 1
                print(num_lines)
                out.write(str(num_lines))
matcher.remove("thatADP")

17860752185314450104 thatADP 3 6 say that in
17860752185314450104 thatADP 2 5 hoping that today
17860752185314450104 thatADP 1 4 say that after
17860752185314450104 thatADP 17 20 praying that the
17860752185314450104 thatADP 2 5 imagined that the
17860752185314450104 thatADP 20 23 saying that it
17860752185314450104 thatADP 11 14 said that a
17860752185314450104 thatADP 3 6 say that week
17860752185314450104 thatADP 24 27 noticed that instead
17860752185314450104 thatADP 1 4 said that it
17860752185314450104 thatADP 11 14 noticed that the
17860752185314450104 thatADP 4 7 suggested that the
17860752185314450104 thatADP 3 6 say that at
17860752185314450104 thatADP 1 4 realized that the
17860752185314450104 thatADP 4 7 noticed that the
17860752185314450104 thatADP 3 6 know that daiquiris
17860752185314450104 thatADP 2 5 heard that before
17860752185314450104 thatADP 3 6 reminded that the
17860752185314450104 thatADP 1 4 said that this
17860752185314450104 thatADP 8 11 say that nothing
178

17860752185314450104 thatADP 9 12 say that such
17860752185314450104 thatADP 1 4 felt that Russians
17860752185314450104 thatADP 1 4 said that city
17860752185314450104 thatADP 3 6 thought that when
17860752185314450104 thatADP 5 8 realize that the
17860752185314450104 thatADP 2 5 realized that it
17860752185314450104 thatADP 10 13 is that you
17860752185314450104 thatADP 8 11 realized that its
17860752185314450104 thatADP 70 73 seemed that at
17860752185314450104 thatADP 28 31 decided that the
17860752185314450104 thatADP 2 5 noticed that the
17860752185314450104 thatADP 14 17 suppose that they
17860752185314450104 thatADP 2 5 see that one
17860752185314450104 thatADP 8 11 saw that tears
17860752185314450104 thatADP 36 39 thought that both
17860752185314450104 thatADP 1 4 thought that this
17860752185314450104 thatADP 1 4 suspected that Grandmother
17860752185314450104 thatADP 37 40 thought that if
17860752185314450104 thatADP 105 108 announced that she
17860752185314450104 thatADP 1 

17860752185314450104 thatADP 2 5 grant that I
17860752185314450104 thatADP 10 13 grant that I
17860752185314450104 thatADP 4 7 doubted that it
17860752185314450104 thatADP 1 4 marveled that he
17860752185314450104 thatADP 37 40 think that a
17860752185314450104 thatADP 3 6 is that later
17860752185314450104 thatADP 5 8 know that Pushkin
17860752185314450104 thatADP 1 4 means that there
17860752185314450104 thatADP 15 18 planned that he
17860752185314450104 thatADP 1 4 knew that it
17860752185314450104 thatADP 11 14 suffered that much
17860752185314450104 thatADP 2 5 felt that he
17860752185314450104 thatADP 20 23 suggested that the
17860752185314450104 thatADP 2 5 reasoned that if
17860752185314450104 thatADP 3 6 made that crashing
17860752185314450104 thatADP 6 9 confirm that she
17860752185314450104 thatADP 10 13 learn that she
17860752185314450104 thatADP 2 5 wrote that she
17860752185314450104 thatADP 30 33 learn that My
17860752185314450104 thatADP 8 11 realize that she
1786075218

17860752185314450104 thatADP 1 4 lookit that fiiiine
17860752185314450104 thatADP 2 5 say that now
17860752185314450104 thatADP 11 14 mention that the
17860752185314450104 thatADP 2 5 think that highly
17860752185314450104 thatADP 23 26 understand that my
17860752185314450104 thatADP 17 20 requested that I
17860752185314450104 thatADP 1 4 explained that there
17860752185314450104 thatADP 32 35 explained that the
17860752185314450104 thatADP 3 6 is that you
17860752185314450104 thatADP 16 19 thinking that Palashkin
17860752185314450104 thatADP 1 4 Is that a
17860752185314450104 thatADP 8 11 noticed that her
17860752185314450104 thatADP 6 9 see that the
17860752185314450104 thatADP 24 27 demanding that it
17860752185314450104 thatADP 103 106 convoluted that when
17860752185314450104 thatADP 1 4 understands that he
17860752185314450104 thatADP 33 36 imagining that it
17860752185314450104 thatADP 3 6 know that the
17860752185314450104 thatADP 83 86 resents that she
17860752185314450104 tha

17860752185314450104 thatADP 9 12 assumed that she
17860752185314450104 thatADP 8 11 imagined that our
17860752185314450104 thatADP 12 15 believe that we
17860752185314450104 thatADP 2 5 expected that my
17860752185314450104 thatADP 19 22 saying that she
17860752185314450104 thatADP 26 29 known that my
17860752185314450104 thatADP 13 16 understood that we
17860752185314450104 thatADP 2 5 suggested that the
17860752185314450104 thatADP 11 14 wished that Janet
17860752185314450104 thatADP 2 5 think that my
17860752185314450104 thatADP 23 26 pretended that it
17860752185314450104 thatADP 11 14 knew that soon
17860752185314450104 thatADP 31 34 say that it
17860752185314450104 thatADP 7 10 pretending that there
17860752185314450104 thatADP 21 24 meant that there
17860752185314450104 thatADP 2 5 credit that the
17860752185314450104 thatADP 12 15 seems that she
17860752185314450104 thatADP 11 14 says that it
17860752185314450104 thatADP 4 7 compote that she
17860752185314450104 thatADP 36 39 

...

17860752185314450104 thatADP 4 7 is that in
17860752185314450104 thatADP 3 6 said that if
17860752185314450104 thatADP 2 5 said that that
17860752185314450104 thatADP 3 6 think that he
17860752185314450104 thatADP 0 3 Learning that her
17860752185314450104 thatADP 5 8 realizes that the
17860752185314450104 thatADP 17 20 realize that my
17860752185314450104 thatADP 7 10 realize that I
17860752185314450104 thatADP 2 5 know that it
17860752185314450104 thatADP 2 5 hear that curly
17860752185314450104 thatADP 2 5 heard that this
17860752185314450104 thatADP 3 6 thought that in
17860752185314450104 thatADP 60 63 produce that intoxicating
17860752185314450104 thatADP 2 5 be that he
17860752185314450104 thatADP 2 5 feared that I
17860752185314450104 thatADP 2 5 suggested that he
17860752185314450104 thatADP 5 8 is that from
17860752185314450104 thatADP 3 6 appeared that Hyon
17860752185314450104 thatADP 2 5 feared that perhaps
17860752185314450104 thatADP 1 4 fear that with
178607521853144501

17860752185314450104 thatADP 2 5 see that she
17860752185314450104 thatADP 6 9 was that he
17860752185314450104 thatADP 3 6 heard that an
17860752185314450104 thatADP 1 4 imagined that as
17860752185314450104 thatADP 2 5 believed that the
17860752185314450104 thatADP 1 4 knew that his
17860752185314450104 thatADP 4 7 imagine that his
17860752185314450104 thatADP 4 7 was that his
17860752185314450104 thatADP 9 12 seemed that the
17860752185314450104 thatADP 5 8 informed that the
17860752185314450104 thatADP 3 6 imagined that the
17860752185314450104 thatADP 5 8 told that a
17860752185314450104 thatADP 32 35 Be that as
17860752185314450104 thatADP 10 13 see that these
17860752185314450104 thatADP 2 5 felt that the
17860752185314450104 thatADP 35 38 realizing that the
17860752185314450104 thatADP 4 7 suppose that an
17860752185314450104 thatADP 6 9 saying that her
17860752185314450104 thatADP 1 4 felt that he
17860752185314450104 thatADP 1 4 seemed that they
17860752185314450104 thatADP 8

17860752185314450104 thatADP 6 9 say that what
17860752185314450104 thatADP 4 7 was that they
17860752185314450104 thatADP 33 36 knew that when
17860752185314450104 thatADP 1 4 say that truly
17860752185314450104 thatADP 2 5 happens that someone
17860752185314450104 thatADP 4 7 think that in
17860752185314450104 thatADP 13 16 convinced that he
17860752185314450104 thatADP 1 4 demanded that I
17860752185314450104 thatADP 1 4 asked that I
17860752185314450104 thatADP 63 66 argue that he
17860752185314450104 thatADP 3 6 was that the
17860752185314450104 thatADP 33 36 explained that her
17860752185314450104 thatADP 33 36 be that the
17860752185314450104 thatADP 10 13 explained that this
17860752185314450104 thatADP 12 15 is that you
17860752185314450104 thatADP 11 14 rumored that Violeta
17860752185314450104 thatADP 12 15 was that demented
17860752185314450104 thatADP 1 4 know that family
17860752185314450104 thatADP 3 6 worried that Violeta
17860752185314450104 thatADP 1 4 think that the


17860752185314450104 thatADP 5 8 realized that the
17860752185314450104 thatADP 15 18 suggest that we
17860752185314450104 thatADP 31 34 say that I
17860752185314450104 thatADP 4 7 knew that I
17860752185314450104 thatADP 2 5 thought that I
17860752185314450104 thatADP 23 26 realized that it
17860752185314450104 thatADP 8 11 thought that it
17860752185314450104 thatADP 35 38 say that we
17860752185314450104 thatADP 14 17 was that she
17860752185314450104 thatADP 16 19 convinced that we
17860752185314450104 thatADP 22 25 was that she
17860752185314450104 thatADP 1 4 reckoned that her
17860752185314450104 thatADP 23 26 granted that when
17860752185314450104 thatADP 33 36 know that she
17860752185314450104 thatADP 3 6 suspected that a
17860752185314450104 thatADP 3 6 imagined that the
17860752185314450104 thatADP 2 5 said that rather
17860752185314450104 thatADP 9 12 decided that Nathalie
17860752185314450104 thatADP 18 21 find that I
17860752185314450104 thatADP 17 20 suggests that her
1

17860752185314450104 thatADP 2 5 believe that we
17860752185314450104 thatADP 12 15 is that what
17860752185314450104 thatADP 3 6 felt that something
17860752185314450104 thatADP 5 8 knew that he
17860752185314450104 thatADP 1 4 realized that his
17860752185314450104 thatADP 2 5 explained that Gubreg
17860752185314450104 thatADP 5 8 say that the
17860752185314450104 thatADP 1 4 knew that the
17860752185314450104 thatADP 2 5 knew that the
17860752185314450104 thatADP 2 5 said that my
17860752185314450104 thatADP 9 12 was that Kopag
17860752185314450104 thatADP 5 8 sensed that this
17860752185314450104 thatADP 1 4 knew that Jero
17860752185314450104 thatADP 2 5 know that when
17860752185314450104 thatADP 1 4 said that they
17860752185314450104 thatADP 3 6 live that long
17860752185314450104 thatADP 3 6 care that the
17860752185314450104 thatADP 10 13 indicating that the
17860752185314450104 thatADP 12 15 realized that he
17860752185314450104 thatADP 2 5 was that Cangkriman
17860752185314

#### Fisher's Exact or verb + 'that' ADP

In [23]:
#verb + thatADP

print('verb + that (ADP)')
print('e.g. said that, hoped that')

#ru
oddsratio, pvalue = scipy.stats.fisher_exact([[339, 79144], [325, 79157]])
print('ru')
print(pvalue)

#pt
oddsratio, pvalue = scipy.stats.fisher_exact([[161, 34369], [141, 34388]])
print('pt')
print(pvalue)

#it
oddsratio, pvalue = scipy.stats.fisher_exact([[202, 36257], [149, 36309]])
print('it')
print(pvalue)

#es
oddsratio, pvalue = scipy.stats.fisher_exact([[234, 35455], [146, 35543]])
print('es')
print(pvalue)

#id
oddsratio, pvalue = scipy.stats.fisher_exact([[159, 20168], [83, 20244]])
print('id')
print(pvalue)

#de
oddsratio, pvalue = scipy.stats.fisher_exact([[190, 44153], [182, 44161]])
print('de')
print(pvalue)

#ko
oddsratio, pvalue = scipy.stats.fisher_exact([[830, 147220], [606, 147443]])
print('ko')
print(pvalue)

verb + that (ADP)
e.g. said that, hoped that
ru
0.6132022081067949
pt
0.27317308924744504
it
0.005324720469178482
es
6.99749011777236e-06
id
1.0948838721222733e-06
de
0.716137121920333
ko
3.4080956017720534e-09


#### 4.7.2 That (determiner)

In [24]:
#ThatDET - real one, with DT tag plus POS det
pattern = [{}, {"LEMMA": "that", "POS": "DET", "TAG": "DT"}, {}]
matcher.add("thatDET", None, pattern)
for filename in os.listdir(sourcefiledirectory):
    if filename.startswith("all"):
        
        f = open(filename, 'r')
        text = f.read()
        lines = sent_tokenize(text)
        outname = filename.replace('all', 'tmp')
        with open(outname, 'w') as out:
            for index,line in enumerate(lines):
                annotated_line = nlp(line)
                matches = matcher(annotated_line)
                for match_id, start, end in matches:
                    string_id = nlp.vocab.strings[match_id]  # Get string representation
                    span = annotated_line[start:end]  # The matched span
                    print(match_id, string_id, start, end, span.text)
                    out.write(str(match_id))
                    out.write("\n")
for filename in os.listdir(sourcefiledirectory):
    if filename.startswith("tmp_"):
        with open(filename, 'r') as f:
            outname = filename.replace('tmp', 'thatDET2')
            num_lines = 0
            with open(outname, 'w') as out:
                for line in f:
                    num_lines += 1
                print(num_lines)
                out.write(str(num_lines))
matcher.remove("thatDET")

1013076350897071439 thatDET 14 17 understood that was
1013076350897071439 thatDET 0 3 After that everyone
1013076350897071439 thatDET 3 6 remember that was
1013076350897071439 thatDET 15 18 like that,
1013076350897071439 thatDET 20 23 certainty that homicide
1013076350897071439 thatDET 3 6 do that.
1013076350897071439 thatDET 11 14 

That was
1013076350897071439 thatDET 9 12 like that anyway
1013076350897071439 thatDET 0 3 Not that sort
1013076350897071439 thatDET 8 11 at that point
1013076350897071439 thatDET 5 8 be that same
1013076350897071439 thatDET 26 29 backgammon that night
1013076350897071439 thatDET 2 5 was that?
1013076350897071439 thatDET 0 3 On that day
1013076350897071439 thatDET 5 8 take that one
1013076350897071439 thatDET 0 3 Put that prizefighter
1013076350897071439 thatDET 2 5 in that empty
1013076350897071439 thatDET 4 7 of that little
1013076350897071439 thatDET 1 4 only that,
1013076350897071439 thatDET 0 3 After that he
1013076350897071439 thatDET 20 23 time that

1013076350897071439 thatDET 4 7 like that,
1013076350897071439 thatDET 7 10 in that stuffy
1013076350897071439 thatDET 3 6 say that?
1013076350897071439 thatDET 20 23 over that which
1013076350897071439 thatDET 14 17 , that double
1013076350897071439 thatDET 1 4 remembered that day
1013076350897071439 thatDET 3 6 of that bum
1013076350897071439 thatDET 26 29 And that’s
1013076350897071439 thatDET 0 3 After that,
1013076350897071439 thatDET 3 6 of that one
1013076350897071439 thatDET 10 13 on that day
1013076350897071439 thatDET 1 4 His that!
1013076350897071439 thatDET 0 3 “That’s
1013076350897071439 thatDET 14 17 about that student
1013076350897071439 thatDET 2 5 beforehand that just
1013076350897071439 thatDET 9 12 of that name
1013076350897071439 thatDET 25 28 me that demagoguery
1013076350897071439 thatDET 0 3 So that was
1013076350897071439 thatDET 9 12 —that’s
1013076350897071439 thatDET 0 3 Earlier that day
1013076350897071439 thatDET 6 9 even that.
1013076350897071439 thatDET 1

1013076350897071439 thatDET 13 16 after that we
1013076350897071439 thatDET 12 15 from that memorable
1013076350897071439 thatDET 17 20 and that altered
1013076350897071439 thatDET 2 5 put that clock
1013076350897071439 thatDET 44 47 until that moment
1013076350897071439 thatDET 84 87 of that house
1013076350897071439 thatDET 8 11 

That’s
1013076350897071439 thatDET 3 6 easier that way
1013076350897071439 thatDET 0 3 On that Sunday
1013076350897071439 thatDET 3 6 herself that question
1013076350897071439 thatDET 0 3 At that time
1013076350897071439 thatDET 19 22 of that Rusalka
1013076350897071439 thatDET 4 7 hear that admission
1013076350897071439 thatDET 16 19 of that marvelous
1013076350897071439 thatDET 7 10 of that idea
1013076350897071439 thatDET 7 10 on that side
1013076350897071439 thatDET 17 20 , that very
1013076350897071439 thatDET 1 4 Since that day
1013076350897071439 thatDET 4 7 have that kind
1013076350897071439 thatDET 20 23 For that,
1013076350897071439 thatDET 27 30 

1013076350897071439 thatDET 4 7 , that's
1013076350897071439 thatDET 5 8 in that time
1013076350897071439 thatDET 1 4 from that moment
1013076350897071439 thatDET 6 9 and that was
1013076350897071439 thatDET 23 26 up that one
1013076350897071439 thatDET 7 10 hke that of
1013076350897071439 thatDET 6 9 when that nice
1013076350897071439 thatDET 2 5 of that you
1013076350897071439 thatDET 13 16 —that is
1013076350897071439 thatDET 1 4 in that capacity
1013076350897071439 thatDET 11 14 write that.
1013076350897071439 thatDET 1 4 n't that right
1013076350897071439 thatDET 4 7 wrote that,
1013076350897071439 thatDET 10 13 like that:
1013076350897071439 thatDET 14 17 like that.
1013076350897071439 thatDET 14 17 from that failure
1013076350897071439 thatDET 0 3 Igorseized that hand
1013076350897071439 thatDET 3 6 of that circle
1013076350897071439 thatDET 3 6 of that which
1013076350897071439 thatDET 12 15 in that same
1013076350897071439 thatDET 2 5 Oblachkin!^ That was
1013076350897071439 t

1013076350897071439 thatDET 5 8 of that?
1013076350897071439 thatDET 7 10 , that seemed
1013076350897071439 thatDET 5 8 of that than
1013076350897071439 thatDET 0 3 After that,
1013076350897071439 thatDET 23 26 and that was
1013076350897071439 thatDET 1 4 dinner that night
1013076350897071439 thatDET 2 5 ’s that?
1013076350897071439 thatDET 7 10 there that month
1013076350897071439 thatDET 4 7 at that while
1013076350897071439 thatDET 15 18 had that skill
1013076350897071439 thatDET 12 15 but that was
1013076350897071439 thatDET 13 16 like that before
1013076350897071439 thatDET 2 5 , that’s
1013076350897071439 thatDET 39 42 were that had
1013076350897071439 thatDET 0 3 Earlier that day
1013076350897071439 thatDET 9 12 later that afternoon
1013076350897071439 thatDET 2 5 mean that.
1013076350897071439 thatDET 23 26 “That’s
1013076350897071439 thatDET 55 58 knock that white
1013076350897071439 thatDET 4 7 before that happened
1013076350897071439 thatDET 8 11 and that sufficed
1013076350

...

1013076350897071439 thatDET 17 20 in that place
1013076350897071439 thatDET 8 11 knowing that...
1013076350897071439 thatDET 2 5 did that for
1013076350897071439 thatDET 5 8 me that information
1013076350897071439 thatDET 7 10 about that place
1013076350897071439 thatDET 4 7 for that moment
1013076350897071439 thatDET 22 25 at that place
1013076350897071439 thatDET 4 7 answer that question
1013076350897071439 thatDET 0 3 "That's
1013076350897071439 thatDET 4 7 judge that origin
1013076350897071439 thatDET 14 17 at that point
1013076350897071439 thatDET 16 19 and that was
1013076350897071439 thatDET 0 3 After that day
1013076350897071439 thatDET 16 19 "That's
1013076350897071439 thatDET 1 4 Is that what
1013076350897071439 thatDET 6 9 of that year
1013076350897071439 thatDET 50 53 —that was
1013076350897071439 thatDET 11 14 island that year
1013076350897071439 thatDET 3 6 of that year
1013076350897071439 thatDET 4 7 in that.
1013076350897071439 thatDET 5 8 like that.
1013076350897071439

1013076350897071439 thatDET 14 17 “That’s
1013076350897071439 thatDET 4 7 regard that quality
1013076350897071439 thatDET 29 32 felon that society
1013076350897071439 thatDET 0 3 “That guy
1013076350897071439 thatDET 9 12 like that of
1013076350897071439 thatDET 1 4 happened that night
1013076350897071439 thatDET 15 18 to that point
1013076350897071439 thatDET 11 14 what that bitch
1013076350897071439 thatDET 4 7 mean that,
1013076350897071439 thatDET 0 3 Beside that old
1013076350897071439 thatDET 8 11 dirty that day
1013076350897071439 thatDET 24 27 in that sense
1013076350897071439 thatDET 28 31  that.
1013076350897071439 thatDET 40 43 “That’s
1013076350897071439 thatDET 4 7 like that?
1013076350897071439 thatDET 44 47 what that saying
1013076350897071439 thatDET 24 27 of that piecemeal
1013076350897071439 thatDET 20 23 with that 
1013076350897071439 thatDET 4 7 market that day
1013076350897071439 thatDET 5 8 with that pheasant
1013076350897071439 thatDET 12 15 , that is
10130763508

1013076350897071439 thatDET 0 3 “That smell
1013076350897071439 thatDET 16 19 of that stink
1013076350897071439 thatDET 9 12 —that is
1013076350897071439 thatDET 5 8 , that faggot
1013076350897071439 thatDET 5 8 wants that killer
1013076350897071439 thatDET 24 27 from that time
1013076350897071439 thatDET 10 13 and that faggot
1013076350897071439 thatDET 3 6 you that to
1013076350897071439 thatDET 7 10 about that Mikel
1013076350897071439 thatDET 1 4 does that mean
1013076350897071439 thatDET 41 44 ’s that.
1013076350897071439 thatDET 20 23 all that Borgian
1013076350897071439 thatDET 5 8 at that bar
1013076350897071439 thatDET 20 23 “That bar
1013076350897071439 thatDET 19 22 see that time
1013076350897071439 thatDET 12 15 patrol that day
1013076350897071439 thatDET 10 13 But that old
1013076350897071439 thatDET 14 17 had that much
1013076350897071439 thatDET 53 56 ‘that poor
1013076350897071439 thatDET 20 23 at that.
1013076350897071439 thatDET 0 3 And that luckless
10130763508970714

1013076350897071439 thatDET 20 23 like that,
1013076350897071439 thatDET 39 42 of that summer
1013076350897071439 thatDET 16 19 in that hospitable
1013076350897071439 thatDET 0 3 And that was
1013076350897071439 thatDET 24 27 along that street
1013076350897071439 thatDET 11 14 in that room
1013076350897071439 thatDET 19 22 of that sloping
1013076350897071439 thatDET 2 5 be that true
1013076350897071439 thatDET 5 8 in that cold
1013076350897071439 thatDET 1 4 all that ugliness
1013076350897071439 thatDET 15 18 , that overcheerful
1013076350897071439 thatDET 19 22 , that false
1013076350897071439 thatDET 2 5 , that was
1013076350897071439 thatDET 16 19 round that corner
1013076350897071439 thatDET 4 7 around that corner
1013076350897071439 thatDET 23 26 will that was
1013076350897071439 thatDET 0 3 By that time
1013076350897071439 thatDET 10 13 of that room
1013076350897071439 thatDET 0 3 On that occasion
1013076350897071439 thatDET 9 12 from that moment
1013076350897071439 thatDET 14 17

1013076350897071439 thatDET 6 9 resembled that of
1013076350897071439 thatDET 0 3 Is that a
1013076350897071439 thatDET 6 9 challenge that of
1013076350897071439 thatDET 4 7 all that,
1013076350897071439 thatDET 0 3 But that’s
1013076350897071439 thatDET 5 8 of that damned
1013076350897071439 thatDET 6 9 of that man
1013076350897071439 thatDET 11 14 killed that afternoon
1013076350897071439 thatDET 0 3 From that night
1013076350897071439 thatDET 12 15 toward that crow
1013076350897071439 thatDET 10 13 o’clock that night
1013076350897071439 thatDET 4 7 from that curious
1013076350897071439 thatDET 0 3 In that very
1013076350897071439 thatDET 9 12 in that library
1013076350897071439 thatDET 12 15 about that eviction
1013076350897071439 thatDET 0 3 And that crow
1013076350897071439 thatDET 21 24 earlier that afternoon
1013076350897071439 thatDET 0 3 At that same
1013076350897071439 thatDET 6 9 in that letter
1013076350897071439 thatDET 9 12 do that!
1013076350897071439 thatDET 6 9 was tha

In [25]:
#that (DET)

print('that (DET)')
print('e.g. half that amount, that language')

#ru
oddsratio, pvalue = scipy.stats.fisher_exact([[561, 158404], [336, 158629]])
print('ru')
print(pvalue)

#pt
oddsratio, pvalue = scipy.stats.fisher_exact([[310, 68749], [146, 68913]])
print('pt')
print(pvalue)

#it
oddsratio, pvalue = scipy.stats.fisher_exact([[249, 72668], [154, 72763]])
print('it')
print(pvalue)

#es
oddsratio, pvalue = scipy.stats.fisher_exact([[312, 71066], [151, 71227]])
print('es')
print(pvalue)

#id
oddsratio, pvalue = scipy.stats.fisher_exact([[137, 40517], [86, 40568]])
print('id')
print(pvalue)

#de
oddsratio, pvalue = scipy.stats.fisher_exact([[248, 88437], [187, 88498]])
print('de')
print(pvalue)

#ko
oddsratio, pvalue = scipy.stats.fisher_exact([[1167, 294932], [625, 295474]])
print('ko')
print(pvalue)

that (DET)
e.g. half that amount, that language
ru
5.1239859412215036e-14
pt
1.0797491656318811e-14
it
2.4820113990199185e-06
es
5.320925598892417e-14
id
0.0007630926580896925
de
0.0039222600251847105
ko
4.563250569968255e-38


### 4.8 X's own construction
Russian has a specific word for "one's own"; we wondered if that construction in English might be more frequent as a result.

In [26]:
#"PRP$'s own'"
pattern = [{"TAG": "PRP$"}, {"orth": "own"}]


matcher.add("own", None, pattern)
for filename in os.listdir(sourcefiledirectory):
    if filename.startswith("all"):
        
        f = open(filename, 'r')
        text = f.read()
        lines = sent_tokenize(text)
        outname = filename.replace('all', 'tmp_')
        with open(outname, 'w') as out:
            print(filename)
            for index,line in enumerate(lines):
                annotated_line = nlp(line)
                matches = matcher(annotated_line)
                for match_id, start, end in matches:
                    string_id = nlp.vocab.strings[match_id]  # Get string representation
                    span = annotated_line[start:end]  # The matched span
                    print(match_id, string_id, start, end, span.text)
                    out.write(str(match_id))
                    out.write("\n")
for filename in os.listdir(sourcefiledirectory):
    if filename.startswith("tmp_"):
        with open(filename, 'r') as f:
            outname = filename.replace('tmp_', 'PRP_own_')
            num_lines = 0
            with open(outname, 'w') as out:
                for line in f:
                    num_lines += 1
                print(filename)
                print(num_lines)
                out.write(str(num_lines))
matcher.remove("own")

all_ru.txt
2646123857127441627 own 8 10 my own
2646123857127441627 own 31 33 my own
2646123857127441627 own 13 15 his own
2646123857127441627 own 25 27 its own
2646123857127441627 own 36 38 my own
2646123857127441627 own 16 18 his own
2646123857127441627 own 15 17 his own
2646123857127441627 own 14 16 his own
2646123857127441627 own 4 6 his own
2646123857127441627 own 24 26 her own
2646123857127441627 own 4 6 her own
2646123857127441627 own 10 12 her own
2646123857127441627 own 2 4 your own
2646123857127441627 own 5 7 your own
2646123857127441627 own 6 8 my own
2646123857127441627 own 5 7 her own
2646123857127441627 own 34 36 their own
2646123857127441627 own 19 21 their own
2646123857127441627 own 2 4 his own
2646123857127441627 own 7 9 his own
2646123857127441627 own 32 34 his own
2646123857127441627 own 4 6 her own
2646123857127441627 own 11 13 her own
2646123857127441627 own 14 16 his own
2646123857127441627 own 11 13 his own
2646123857127441627 own 16 18 his own
264612385712744162

2646123857127441627 own 25 27 his own
2646123857127441627 own 10 12 his own
2646123857127441627 own 5 7 his own
2646123857127441627 own 32 34 his own
2646123857127441627 own 8 10 my own
2646123857127441627 own 14 16 its own
2646123857127441627 own 3 5 his own
2646123857127441627 own 5 7 your own
2646123857127441627 own 27 29 his own
2646123857127441627 own 5 7 its own
2646123857127441627 own 9 11 her own
2646123857127441627 own 4 6 his own
2646123857127441627 own 23 25 her own
2646123857127441627 own 7 9 his own
2646123857127441627 own 8 10 her own
2646123857127441627 own 9 11 her own
2646123857127441627 own 9 11 his own
2646123857127441627 own 12 14 her own
2646123857127441627 own 2 4 his own
2646123857127441627 own 0 2 His own
2646123857127441627 own 41 43 his own
2646123857127441627 own 36 38 his own
2646123857127441627 own 10 12 his own
2646123857127441627 own 20 22 your own
2646123857127441627 own 16 18 my own
2646123857127441627 own 21 23 his own
2646123857127441627 own 10 12 you

2646123857127441627 own 5 7 his own
2646123857127441627 own 8 10 his own
2646123857127441627 own 29 31 our own
2646123857127441627 own 22 24 their own
2646123857127441627 own 5 7 his own
2646123857127441627 own 5 7 his own
2646123857127441627 own 13 15 her own
2646123857127441627 own 17 19 your own
2646123857127441627 own 5 7 your own
2646123857127441627 own 15 17 my own
2646123857127441627 own 22 24 my own
2646123857127441627 own 37 39 my own
2646123857127441627 own 41 43 my own
2646123857127441627 own 12 14 my own
2646123857127441627 own 18 20 my own
2646123857127441627 own 16 18 my own
2646123857127441627 own 25 27 my own
2646123857127441627 own 16 18 my own
2646123857127441627 own 22 24 my own
2646123857127441627 own 15 17 my own
2646123857127441627 own 26 28 its own
2646123857127441627 own 4 6 my own
2646123857127441627 own 6 8 his own
2646123857127441627 own 18 20 his own
2646123857127441627 own 17 19 his own
2646123857127441627 own 24 26 his own
2646123857127441627 own 8 10 his 

2646123857127441627 own 5 7 my own
2646123857127441627 own 10 12 her own
2646123857127441627 own 9 11 their own
2646123857127441627 own 9 11 its own
2646123857127441627 own 5 7 her own
2646123857127441627 own 27 29 his own
2646123857127441627 own 31 33 her own
2646123857127441627 own 27 29 my own
2646123857127441627 own 41 43 his own
2646123857127441627 own 7 9 his own
2646123857127441627 own 44 46 her own
2646123857127441627 own 17 19 his own
2646123857127441627 own 29 31 our own
2646123857127441627 own 35 37 my own
2646123857127441627 own 20 22 your own
2646123857127441627 own 24 26 your own
2646123857127441627 own 16 18 my own
2646123857127441627 own 12 14 her own
2646123857127441627 own 5 7 our own
2646123857127441627 own 28 30 their own
2646123857127441627 own 16 18 his own
2646123857127441627 own 7 9 my own
2646123857127441627 own 2 4 your own
2646123857127441627 own 9 11 my own
2646123857127441627 own 26 28 his own
2646123857127441627 own 32 34 her own
2646123857127441627 own 32

In [27]:
#One's own

#ru
print('determiner + own')
print('e.g. his own')
oddsratio, pvalue = scipy.stats.fisher_exact([[148, 79335], [105, 79377]])
print('ru')
print(pvalue)

#pt
oddsratio, pvalue = scipy.stats.fisher_exact([[22, 34508], [46, 34484]])
print('pt')
print(pvalue)

#it
oddsratio, pvalue = scipy.stats.fisher_exact([[37, 36422], [48, 36410]])
print('it')
print(pvalue)

#es
oddsratio, pvalue = scipy.stats.fisher_exact([[37, 35652], [47, 35642]])
print('es')
print(pvalue)

#id
oddsratio, pvalue = scipy.stats.fisher_exact([[37, 35652], [27, 20300]])
print('id')
print(pvalue)

#de
oddsratio, pvalue = scipy.stats.fisher_exact([[37, 35652], [59, 44284]])
print('de')
print(pvalue)

#ko
oddsratio, pvalue = scipy.stats.fisher_exact([[37, 35652], [196, 147854]])
print('ko')
print(pvalue)

determiner + own
e.g. his own
ru
0.008100240837848258
pt
0.004882593776686034
it
0.2351032721200506
es
0.32584874452491813
id
0.36274589527796686
de
0.2588442674122063
ko
0.18519019009229035


### 4.9 Person entities
For this, I ran Stanford CoreNLP NER on each of the corpus files, and counted the number of PERSON entities, then added it to the Excel spreadsheet to get values for Fisher's exact, below.

In [28]:
#ru
oddsratio, pvalue = scipy.stats.fisher_exact([[3300, 155665], [4230, 154735]])
print('ru')
print(pvalue)

#pt
oddsratio, pvalue = scipy.stats.fisher_exact([[847, 68212], [1838, 67221]])
print('pt')
print(pvalue)

#it
oddsratio, pvalue = scipy.stats.fisher_exact([[909, 72008], [1940, 70977]])
print('it')
print(pvalue)

#es
oddsratio, pvalue = scipy.stats.fisher_exact([[1298, 70080], [1899, 69479]])
print('es')
print(pvalue)

#id
oddsratio, pvalue = scipy.stats.fisher_exact([[860, 39794], [1082, 39572]])
print('id')
print(pvalue)

#de
oddsratio, pvalue = scipy.stats.fisher_exact([[905, 87780], [2360, 86325]])
print('de')
print(pvalue)

#ko
oddsratio, pvalue = scipy.stats.fisher_exact([[2830, 293269], [7879, 288220]])
print('ko')
print(pvalue)

ru
2.033189652779931e-27
pt
7.545057573933009e-85
it
1.9003428803047667e-86
es
5.1267874919296124e-27
id
3.752344416753503e-07
de
1.5462813004649626e-150
ko
0.0
